In [0]:
%sh
pip install spacy
pip install habanero
python -m spacy download en_core_web_sm

  Attempting uninstall: typing-extensions
    Found existing installation: typing-extensions 4.1.1
    Not uninstalling typing-extensions at /databricks/python3/lib/python3.9/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-0967e4df-473f-4425-a830-6e8d5d667db4
    Can't uninstall 'typing-extensions'. No files were found to uninstall.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-0967e4df-473f-4425-a830-6e8d5d667db4/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-0967e4df-473f-4425-a830-6e8d5d667db4/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-0967e4df-473f-4425-a830-6e8d5d667db4/bin/python -m pip install --upgrade pip' command.
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')


In [0]:
dbutils.library.restartPython()

In [0]:
from pyspark.sql.types import StringType, IntegerType, ArrayType
import time
import pyspark.sql.functions as F
from pyspark.sql import Window
import requests
import json
import urllib.parse
import spacy

#### Database Schema

<img src="https://i.ibb.co/hRqLR8d/Schema.png" alt="Schema" border="0">

In [0]:
raw_df = spark.read.format("delta").load("/user/hive/warehouse/scientific_publications")
display(raw_df.limit(5))

_id abstract authors doi fos isbn issn issue keywords lang n_citation page_end page_start pdf references title url venue volume year 53e99784b7602d9701f3e3f5 null null null null null null null List() en 0 null null null null 3GIO. null List(null, null, null, null, null, null, null, null, null, null, null, null, 0) null 2011 53e99784b7602d9701f3e133 Drought is the first place in all the natural disasters in the world. It is especially serious in North China Plain. In this paper, different soil water content control levels at winter wheat growth stages are performed on Gucheng Ecological-Meteorological Integrated Observation Experiment Station of CAMS, China. Some canopy parameters, including growth conditions, dry weight, physiological parameters and hyperspectral reflectance, are measured from erecting stage to milk stage for winter wheat in 2009. The relationship between canopy parameters and soil relative moisture, canopy water content and water indices of winter wheat are established. The results show that some parameters, such as SPAD and dry weight of leaves, decrease with the increasing of soil relative moisture, while other parameters, including dry weight of caudexes, above ground dry weight, height, photosynthesis rate, intercellular CO 2 concentration, stomatal conductance and transpiration rate, increase corresponding to the soil relative moisture. Obvious linear relationship between stomatal conductance and transpiration rate is established with 45 samples, which R2 reaches to 0.6152. Finally, the fitting equations between canopy water content and water indices are regressed with b5, b6 and b7 of MODIS bands. The equations are best with b7 and worst with b5. So the fitting equations with b7 can be used to inverse the canopy water content of winter wheat using MODIS or other remote sensing images with similar bands range to MODIS in Hebei Province. © 2011 IEEE. List(List(53f45728dabfaec09f209538, null, null, null, Peijuan Wang, null, null, null, null, null, null, null, null, null, null), List(5601754345cedb3395e59457, null, null, null, Jiahua Zhang, null, null, null, null, null, null, null, null, null, null), List(53f38438dabfae4b34a08928, null, null, null, Donghui Xie, null, null, null, null, null, null, null, null, null, null), List(5601754345cedb3395e5945a, null, null, null, Yanyan Xu, null, null, null, null, null, null, null, null, null, null), List(53f43d25dabfaeecd6995149, null, null, null, Yun Xu, null, null, null, null, null, null, null, null, null, null)) 10.1109/IGARSS.2011.6049503 List(Agronomy, Moisture, Hydrology, Environmental science, Dry weight, Water content, Stomatal conductance, Transpiration, Irrigation, Soil water, Canopy) null List(canopy parameters, canopy spectrum, different soil water content control, winter wheat, irrigation, hydrology, radiometry, moisture, indexes, vegetation, indexation, dry weight, soil moisture, water content, indexing terms, spectrum, natural disaster) en 0 1933 1930 null null The relationship between canopy parameters and spectrum of winter wheat under different irrigations in Hebei Province. List(http://dx.doi.org/10.1109/IGARSS.2011.6049503) List(53a7297d20f7420be8bd4ae7, null, null, International Geoscience and Remote Sensing Symposium, null, null, null, IGARSS, null, null, null, null, 0) null 2011 53e99784b7602d9701f3e151 List(List(53f46797dabfaeb22f542630, null, null, null, Jairo Rocha, null, null, null, null, null, null, null, null, null, null), List(54328883dabfaeb4c6a8a699, null, null, null, Theo Pavlidis, null, null, null, null, null, null, null, null, null, null)) 10.1109/ICDAR.1993.395663 List(Intelligent character recognition, Pattern recognition, Computer science, Feature (computer vision), Document processing, Handwriting recognition, Optical character recognition, Feature extraction, Feature (machine learning), Artificial intelligence, Intelligent word recognition) List(handwriting recognition, prototypes, image segmentation, computer science, expert s

In [0]:
#Filter out titles that have less than 2 words
filtered_df = raw_df.withColumn("title_word_count", F.size(F.split("title", " "))).filter("title_word_count > 1")
display(filtered_df.limit(25))

_id abstract authors doi fos isbn issn issue keywords lang n_citation page_end page_start pdf references title url venue volume year title_word_count 53e99967b7602d97021a560a Ab initio predictions of secondary structures in proteins have to combine local predictions, based on short fragments of the protein sequence, with consistency restrictions, as not all locally plausible predictions may be simultaneously true. We use the fact that secondary structures are patterns of hydrogen bonds and that a single residue can participate in hydrogen bonds of at most one secondary structure. Consistency of fixed-sized pieces of secondary structures is the easiest to approximate and we formalize it as 1-2 matching problem. Consistency of entire secondary structures is a version of set packing. We also investigate how to form a simple problem if we add the requirement that the secondary structure and the loops that connect them fit together in a metric space. Every problem that we investigated is MAX-SNP hard and it has a constant factor approximation. Computational experience suggests that in biological instances, we can find nearly optimal solutions using heuristics. List(List(53f45d3adabfaee0d9c0cb90, null, berman@cse.psu.edu, 5b86b6c2e1cd8e14a34ca959, Piotr Berman, null, null, null, null, The Pennsylvania State University, University Park, PA, USA, null, 5f71b2d91c455f439fe3eb4f, List(Penn State Univ, University Pk, PA 16802 USA), null, null), List(53f436cbdabfaedf43582e9f, null, null, 5b86b6c2e1cd8e14a34ca959, Jieun Jeong, null, null, null, null, The Pennsylvania State University, University Park, PA, USA, null, 5f71b2d91c455f439fe3eb4f, List(Penn State Univ, University Pk, PA 16802 USA), null, null)) 10.1007/s00453-007-9068-8 List(Algorithm, Heuristics, Set packing, Metric space, Ab initio, Hydrogen bond, Protein secondary structure, Mathematics, Protein structure, Theory of computation) 0178-4617 1 List(Secondary Structure, Maximum Weight, Local Prediction, Horizontal Edge, Connector Edge) en 2 34 16 null List(53e9bdcdb7602d9704a7e6ae, 53e99d5eb7602d970261a1c4, 53e9bdcdb7602d9704a7e6ae, 53e99e3eb7602d970270422e, 53e9adffb7602d970380a762, 53e9b593b7602d97040d9071, 53e99c6fb7602d9702522122, 55a43e58612ca648688dc943, 53e99822b7602d97020431be) Consistent Sets of Secondary Structures in Proteins List(http://dx.doi.org/10.1007/s00453-007-9068-8, http://dx.doi.org/https://doi.org/10.1007/s00453-007-9068-8, https://link.springer.com/article/10.1007/s00453-007-9068-8, https://dl.acm.org/citation.cfm?id=3118965&picked=prox&preflayout=flat, http://www.webofknowledge.com/) List(539078f220f770854f5a882f, null, null, null, null, null, null, Algorithmica, null, null, null, null, 0) 53 2009 7 53e99960b7602d97021a53fa In this work a new method of feature extraction for an interactive and adaptive recognizer for on-line handwritten alphanumeric characters has been proposed. The system is suitable for use in conjunction with magnetic pen based devices for inputting data to a data processing system or a computer terminal. The features are extracted from dynamically changing locations of the writing device. The new method of feature extraction is simple, computationally light and fast enough for adaptive on-line use. Extracted features are robust with respect to all possible distortions like shape, size, and orientation. For simulation experiment, numerals 0-9 are used. A single hidden layer feed forward neural network trained by Quickprop algorithm, a variation of error back propagation is used for recognition. Very high recognition rates, even for highly distorted samples have been achieved confirming high generalization capability of the extracted feature set. List(List(53f36626dabfae4b3499aa7a, null, null, 5b86b9c0e1cd8e14a3625bbe, Basabi Chakraborty, null, null, null, null, Faculty of Software and Information Science, Iwate Prefectural University, 152-52 Aza Sugo, Takizawamura, Iwate 020-0193, Japan, null, 5f71b4211c455f439fe47d1e, List(Faculty of S

## Authors

In [0]:
def get_author_from_dblp(title, rank):
    URL = "http://dblp.org/search/publ/api?q=" + title.replace(" ", "+") + "&format=json"
    try:
        r = requests.get(url = URL)
        data = r.json()
        return data['result']['hits']['hit'][0]['info']['authors']['author'][rank-1]['text']
    except:
        return None

In [0]:
authors = (filtered_df.limit(1000).select("doi", "authors", "title", F.posexplode(F.col("authors")).alias("rank", "authors_exp"))
            .withColumn("rank", F.col("rank") + 1)
            .select("authors_exp.*","*")
            .select("doi", "rank", "name", "title")
            .withColumn("name", F.initcap(F.col("name")))
            )

authors2 = authors.filter(F.col("name").rlike(r"^\p{L}\.?(-\p{L}\.?)?\s.+"))
authors_rdd = authors2.rdd.map(lambda x: (x[0], x[1], x[2], x[3], get_author_from_dblp(x[3], x[1])))
authors2 = authors_rdd.toDF(["doi", "rank", "name", "title", "dblp_name"])
    
authors2 = (authors2.withColumn("dblp_name", F.when(F.col("dblp_name") == "null", F.col("name")).otherwise(F.col("dblp_name")))
           .withColumn("dblp_name", F.regexp_extract(F.col("dblp_name"), r"^(\D+)(\s\d\d\d\d)?$", 1)))

authors_raw = (authors.withColumn("dblp_name", F.col("name"))
           .union(authors2)
           .withColumn("last_name_raw", F.regexp_extract(F.col("name"), r"^.+\s(\S+)(\sJr\.)?$", 1))
           .withColumn("dblp_name", F.when(F.col("dblp_name") == "null", F.col("name")).otherwise(F.col("dblp_name")))
           .withColumn("dblp_name", F.regexp_extract(F.col("dblp_name"), r"^(\D+)(\s\d\d\d\d)?$", 1))
           .withColumn("dblp_last_name", F.regexp_extract(F.col("dblp_name"), r"^.+\s(\S+)(\sJr\.)?$", 1))
           .withColumn("name", F.when(F.col("last_name_raw") == F.col("dblp_last_name"), 
                                      F.col("dblp_name")).otherwise(F.col("name")))
           .withColumn("first_name", F.regexp_extract(F.col("name"), r"^(\S+)\s.+$", 1))
           .withColumn("last_name", F.regexp_extract(F.col("name"), r"^.+\s(\S+)$", 1))
           .withColumn("middle_name", F.regexp_extract(F.col("name"), r"^\S+\s(\S+)\s\S+$", 1))
          )

authors = (authors_raw.select("first_name", "last_name", "middle_name")
            .dropDuplicates()
            .withColumn("author_id", F.monotonically_increasing_id())
          )

authors = (authors_raw.join(authors, ["first_name", "last_name", "middle_name"])
           .select("author_id", "first_name", "last_name", "middle_name", "title", F.col("name").alias("author"), "rank")
           .dropDuplicates()
          )

display(authors)

authors_clean = authors.select("author_id", "first_name", "last_name", "middle_name")
authors_clean.write.format("delta").mode("overwrite").saveAsTable("authors")

author_id first_name last_name middle_name title author rank 0 Andreas Herzig Dynamic Logic of Propositional Assignments: A Well-Behaved Variant of PDL Andreas Herzig 2 1 Fu-lai Chung Stock time series pattern matching: Template-based vs. rule-based approaches Fu-lai Chung 2 2 Roberto Barbuti Compositional semantics of spiking neural P systems Roberto Barbuti 1 2 Roberto Barbuti LORETO: a tool for reducing state explosion in verification of LOTOS programs Roberto Barbuti 1 3 Ee-peng Lim An Overview of the Agent-Based Electronic Commerce System (ABECOS) Project Ee-peng Lim 1 4 Chae-woo Yoo Connect with things through instant messaging Chae-woo Yoo 2 5 Wencheng Wang A Multi-focus Image Fusion Method Based on Laplacian Pyramid. Wencheng Wang 1 6 Wanda Pratt Brainstorming Design for Health: Helping Patients Utilize Patient-Generated Information on the Web. Wanda Pratt 12 7 Naoki Nakashima Applicability of Portable Health Clinic to Ageing Society. Naoki Nakashima 5 8 Zena Ariola M. From Syntactic Theories to Interpreters: Automating the Proof of Unique Decomposition Zena M. Ariola 3 9 Niels Bouvin Olof User defined structural searches in mediawiki Niels Olof Bouvin 2 10 Ali Makhdoumi Privacy-utility tradeoff under statistical uncertainty. Ali Makhdoumi 1 11 Nobuo Noda Numerical Analysis of Blood Flow in Vessels Nobuo Noda 1 12 J. Rahayu Wenny The New Object-Relational Generation and its Application in Web Databases J. Wenny Rahayu 1 13 Tereza Iofciu L3S at INEX 2007: Query Expansion for Entity Ranking Using a Highly Accurate Ontology Tereza Iofciu 3 14 Ravi Sundaram Secure and scalable match: overcoming the universal circuit bottleneck using group programs. Ravi Sundaram 2 15 Qingtang Liu Research on DRM-enabled learning objects model Qingtang Liu 1 16 Baruch Mazor A trellis code construction and coding theorem for stationary Gaussian sources Baruch Mazor 1 17 Vaishak Belle A Semantical Account of Progression in the Presence of Uncertainty. Vaishak Belle 1 18 Chong Wang On the Mutual Information Between Interaction Perplexity and Function of Proteins Chong Wang 6 19 Amara Amara Read Stability and Write Ability Tradeoff for 6T SRAM Cells in Double-Gate CMOS Amara Amara 2 20 Silke Witt M. A Comparison of Dialog Strategies for Call Routing Silke M. Witt 2 21 Xu Wu A destination information based probabilistic routing protocol for vehicular sensor networks Xu Wu 2 22 Shi-an Chen Fuzzy adaptive synchronization of time-reversed chaotic systems via a new adaptive control strategy Shi-an Chen 3 23 Greig Zubicaray Fluid Registration of Diffusion Tensor Images Using Information Theory Greig I. De Zubicaray 8 24 P. Wang Bifurcation of Equilibrium in Micromachined Elastic Structures with Liquid Interface P. K. C. Wang 1 25 Ying Liu Theoretical study of structure and lattice vibrations of R3Co11-xFexB4 (R=Nd, Gd). Ying Liu 4 26 Han-chin Cheng Custos Remote on-demand healthcare aided with wireless sensors and mobile phones. Han-chin Cheng 5 27 Weiwu Shi Communication with Threads in Software DSMs Weiwu Hu Gang Shi 1 28 Jesus Carretero An ontology-driven decision support system for high-performance and cost-optimized design of complex railway portal frames Jesus Carretero 4 29 Serge Tichkiewitch Fostering Innovation and Entrepreneurship in European VET: EU Project "From Idea to Enterprise". Serge Tichkiewitch 13 30 Shunsuke Araki Improvement of Tseng et al.'s authenticated encryption scheme with message linkages Shunsuke Araki 2 31 Harold Thiele The Dublin Core and Warwick Framework:A Review of the Literature, March 1995 - September 1997 Harold Thiele 1 32 Kazuo Takahata Evaluation of Cognitive Wireless Networks in Rural Area for Disaster Information Network Kazuo Takahata 2 33 Kyung Sun Pseudo-organ boundary conditions applied to a computational fluid dynamics model of the human aorta Kyung Sun 4 34 Hitoshi Kino Application of Cylindrical Elastic Elements for Stiffness Control of Tendon-Driven Manipulator and Inverse Kinematics Evaluation Hitosh

## Organizations

In [0]:
def get_organization(name, country):
    try:
        URL = "https://api.ror.org/organizations?query=" + name.replace(" ", "+")
        r = requests.get(url = URL)
        data = r.json()
        if data['number_of_results'] == 0:
            return "No results"
        for i in range(data['number_of_results']):
            found_country = data['items'][i]["country"]["country_name"]
            if country == "" or country == found_country:
                return data['items'][i]["name"]+";"+data['items'][i]["addresses"][0]["city"]+";"+found_country
    except:
        return "No results"

In [0]:
countries = "(,|\s)(Afghanistan|Albania|Algeria|Andorra|Angola|Antigua and Barbuda|Argentina|Armenia|Australia|Austria|Azerbaijan|Bahamas|Bahrain|Bangladesh|Barbados|Belarus|Belgium|Belize|Benin|Bhutan|Bolivia|Bosnia and Herzegovina|Botswana|Brazil|Brunei|Bulgaria|Burkina Faso|Burundi|Cabo Verde|Cambodia|Cameroon|Canada|Central African Republic|Chad|Chile|China|Colombia|Comoros|Democratic Republic of the Congo|Republic of the Congo|Costa Rica|Cote d'Ivoire|Croatia|Cuba|Cyprus|Czech Republic|Denmark|Djibouti|Dominica|Dominican Republic|Ecuador|Egypt|El Salvador|Equatorial Guinea|Eritrea|Estonia|Ethiopia|Fiji|Finland|France|Gabon|Gambia|Georgia|Germany|Ghana|Greece|Grenada|Guatemala|Guinea|Guinea-Bissau|Guyana|Haiti|Honduras|Hungary|Iceland|India|Indonesia|Iran|Iraq|Ireland|Israel|Italy|Jamaica|Japan|Jordan|Kazakhstan|Kenya|Kiribati|Kosovo|Kuwait|Kyrgyzstan|Laos|Latvia|Lebanon|Lesotho|Liberia|Libya|Liechtenstein|Lithuania|Luxembourg|North Macedonia|Madagascar|Malawi|Malaysia|Maldives|Mali|Malta|Marshall Islands|Mauritania|Mauritius|Mexico|Micronesia|Moldova|Monaco|Mongolia|Montenegro|Morocco|Mozambique|Myanmar|Namibia|Nauru|Nepal|Netherlands|New Zealand|Nicaragua|Niger|Nigeria|North Korea|Norway|Oman|Pakistan|Palau|Palestine|Panama|Papua New Guinea|Paraguay|Peru|Philippines|Poland|Portugal|Qatar|Romania|Russia|Rwanda|Saint Kitts and Nevis|Saint Lucia|Saint Vincent and the Grenadines|Samoa|San Marino|Sao Tome and Principe|Saudi Arabia|Senegal|Serbia|Seychelles|Sierra Leone|Singapore|Slovakia|Slovenia|Solomon Islands|Somalia|South Africa|South Korea|South Sudan|Spain|Sri Lanka|Sudan|Suriname|Swaziland|Sweden|Switzerland|Syria|Taiwan|Tajikistan|Tanzania|Thailand|Timor-Leste|Togo|Tonga|Trinidad and Tobago|Tunisia|Turkey|Turkmenistan|Tuvalu|Uganda|Ukraine|United Arab Emirates|UAE|United Kingdom|UK|United States of America|USA|United States|US|Uruguay|Uzbekistan|Vanuatu|Vatican City|Venezuela|Vietnam|Yemen|Zambia|Zimbabwe)(,|\s|$)"


organization = (filtered_df.limit(1000).select("authors", "title", F.explode(F.col("authors")).alias("authors_exp"))
               .select("authors_exp.*","*")
               .withColumn("author", F.col("name"))
               .select("author", "org")
               .filter(F.col("org").isNotNull())
               .dropDuplicates()
                # ., +, *, ?, ^, $, (, ), [, ], {, }, |, \
               .withColumn("strip_org", F.regexp_replace(F.col("org"), r'[\+-=#&\|><!\(\)\{\}\[\]\^"~\*\?:\\/]', " "))
               .withColumn("county", F.regexp_extract(F.col("org"), countries, 2))
               .withColumn("county", F.regexp_replace("county", "United States of America|USA|US", "United States"))
               .withColumn("county", F.regexp_replace("county", "UK", "United Kingdom"))
               .withColumn("county", F.regexp_replace("county", "UAE", "United Arab Emirates"))
               )

organization_rdd = organization.rdd.map(lambda x: (x[0], x[1], x[2], x[3], get_organization(x[2], x[3])))
organization_raw = (organization_rdd.toDF(["author", "org", "strip_org", "country", "api_org"])
                    .withColumn("api_name", F.regexp_extract(F.col("api_org"), r"^(.+);.+;.+$", 1))
                    .withColumn("match", F.expr(r"regexp_extract(org, concat('(', api_name,')'), 0)"))
                    .withColumn("name", F.when(F.col("match") == "", F.col("org"))
                               .otherwise(F.col("api_name")))
                    .withColumn("city", F.when(F.col("match") == "", "")
                               .otherwise(F.regexp_extract(F.col("api_org"), r"^.+;(.+);.+$", 1)))
                    .withColumn("country", F.when(F.col("match") == "", F.col("country"))
                               .otherwise(F.regexp_extract(F.col("api_org"), r"^.+;.+;(.+)$", 1)))
                   )

organization = (organization_raw.select("name", "city", "country")
                .dropDuplicates()
                .withColumn("org_id", F.monotonically_increasing_id())
               )

organization = (organization_raw.join(organization, ["name", "city", "country"])
                .select("org_id", "name", "city", "country", "author"))

display(organization)

organization_clean = organization.select("org_id", "name", "city", "country")
organization_clean.write.format("delta").mode("overwrite").saveAsTable("organization")

org_id name city country author 0 Vrije Universiteit Amsterdam Amsterdam Netherlands Henri E. Bal 1 Tel.: +44 7786 317995. Nigel Jones 2 Advanced Broadcast Systems Development, Division, NEC 10, Nisshin-cho 1-chome, Fuchu, Tokyo 183-6501, Japan Japan Kazutoshi Maeno 3 Univ Wisconsin, Madison, WI USA United States Kathy A. Johnson 3 Univ Wisconsin, Madison, WI USA United States Patricia Flatley Brennan 4 National Institute of Mental Health Bethesda United States Brooke A Babineau 4 National Institute of Mental Health Bethesda United States Jacqueline N Crawley 5 university of pavia Elena Molho 6 ST Microelectronics, Cornaredo Francesco Papariello 6 ST Microelectronics, Cornaredo Giuseppe Desoli 7 BTexact Technologies Content and Coding Lab Adastral Park Ipswich UK United Kingdom David J. Chatting 7 BTexact Technologies Content and Coding Lab Adastral Park Ipswich UK United Kingdom Jeremy M. Thorne 8 Tokyo Inst. Tech., Yokohama, Japan Japan Takao Terano 9 Member, IEEE Xu Zhu 10 Laboratory of Visual Information Processing, Institute of Biophysics, Chinese Academy of Sciences, Beijing 100101, P.R. China CN China Z Wu 10 Laboratory of Visual Information Processing, Institute of Biophysics, Chinese Academy of Sciences, Beijing 100101, P.R. China CN China Z Gong 10 Laboratory of Visual Information Processing, Institute of Biophysics, Chinese Academy of Sciences, Beijing 100101, P.R. China CN China C Feng 10 Laboratory of Visual Information Processing, Institute of Biophysics, Chinese Academy of Sciences, Beijing 100101, P.R. China CN China A Guo 11 University of Bari "Aldo Moro" Via E. Orabona, Bari, Italy Italy Annalina Caputo 11 University of Bari "Aldo Moro" Via E. Orabona, Bari, Italy Italy Pierpaolo Basile 11 University of Bari "Aldo Moro" Via E. Orabona, Bari, Italy Italy Giovanni Semeraro 12 University of Massachusetts at Amherst, Amherst, MA, USA United States Daniel S. Menasché 12 University of Massachusetts at Amherst, Amherst, MA, USA United States Dennis Goeckel 12 University of Massachusetts at Amherst, Amherst, MA, USA United States Don Towsley 13 School of Computing, Soongsil University, Seoul, Korea Chae-Woo Yoo 14 Université Paris 13, Villetaneuse, France France Aurélien Bossard 15 Chonbuk National University Division of Mathematics and Statistical Informatics 561-756 Jeonju Korea 561-756 Jeonju Korea In-kwon Yeo 16 Linköping University Linköping Sweden Ou Tang 17 School of Engineering, Universidad Autonoma de Madrid, Spain Spain Gustavo Sutter 18 University of Massachusetts Howard A. Peelle 19 ITAKA (Intelligent Technologies for Advanced Knowledge Acquisition) Department of Computer Science and Mathematics, University Rovira i Virgili, Tarragona, 43007 David Sánchez 19 ITAKA (Intelligent Technologies for Advanced Knowledge Acquisition) Department of Computer Science and Mathematics, University Rovira i Virgili, Tarragona, 43007 David Isern 19 ITAKA (Intelligent Technologies for Advanced Knowledge Acquisition) Department of Computer Science and Mathematics, University Rovira i Virgili, Tarragona, 43007 Ángel Rodríguez 19 ITAKA (Intelligent Technologies for Advanced Knowledge Acquisition) Department of Computer Science and Mathematics, University Rovira i Virgili, Tarragona, 43007 Antonio Moreno 20 Union College, Schenectady, USA United States John Rieffel 20 Union College, Schenectady, USA United States Schuyler Smith 21 Indian Institute of Technology Bombay Mumbai India Shivam Agarwal 22 Computer and Information Sciences|University of Delaware Lori L. Pollock 23 Korea Artificial Organ Center, Korea University, Seoul, Republic of Korea Chang Mo Hwang 24 Georgia Institute of Technology Atlanta United States Farshid Delgosha 24 Georgia Institute of Technology Atlanta United States Erman Ayday 24 Georgia Institute of Technology Atlanta United States Faramarz Fekri 25 Eindhoven Univ Technol, Dept Elect Engn, POB 513, NL-5600 MB Eindhoven, Netherlands Netherlands Brian Bloemendal 25 Eindhoven Univ Technol, Dept Elect Engn

## Publications

In [0]:
publication_raw = filtered_df.limit(1000).select("_id", "title", "volume", "n_citation", "doi", "url")

display(publication_raw)

_id title volume n_citation doi url 53e99967b7602d97021a560a Consistent Sets of Secondary Structures in Proteins 53 2 10.1007/s00453-007-9068-8 List(http://dx.doi.org/10.1007/s00453-007-9068-8, http://dx.doi.org/https://doi.org/10.1007/s00453-007-9068-8, https://link.springer.com/article/10.1007/s00453-007-9068-8, https://dl.acm.org/citation.cfm?id=3118965&picked=prox&preflayout=flat, http://www.webofknowledge.com/) 53e99960b7602d97021a53fa A new feature extraction technique for on-line recognition of handwritten alphanumeric characters 148 19 10.1016/S0020-0255(02)00276-1 List(http://dx.doi.org/10.1016/S0020-0255(02)00276-1, https://www.sciencedirect.com/science/article/pii/S0020025502002761) 53e99960b7602d97021a5416 King John Divided 19 0 10.1093/llc/19.2.181 List(http://dx.doi.org/10.1093/llc/19.2.181) 53e99960b7602d97021a541f Peer Assist Live Streaming Overlay for Next-Generation-Networks 1 0 10.4018/jhcr.2010100102 List(http://dx.doi.org/10.4018/jhcr.2010100102, http://dx.doi.org/10.4018/978-1-4666-0921-1.ch017) 53e99960b7602d97021a5427 Paramecium: Assembling Raw Nodes into Composite Cells 3222 2 10.1007/978-3-540-30141-7_67 List(http://dx.doi.org/10.1007/978-3-540-30141-7_67, http://www.webofknowledge.com/) 53e99967b7602d97021a5645 Radar Signal Retrodiffusion by Water Surface 2 1 10.1109/IGARSS.2009.5418122 List(http://dx.doi.org/10.1109/IGARSS.2009.5418122, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=5418122) 53e99960b7602d97021a543e Custos Remote on-demand healthcare aided with wireless sensors and mobile phones. 5 10.1109/ICSMC.2008.4811630 List(http://dx.doi.org/10.1109/ICSMC.2008.4811630, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=4811630) 53e99967b7602d97021a566b Group Elevator Scheduling with Advanced Traffic Information for Normal Operations and Coordinated Emergency Evacuation 13 10.1109/ROBOT.2005.1570314 List(http://dx.doi.org/10.1109/ROBOT.2005.1570314) 53e99960b7602d97021a5451 Weighted census transform for feature representation 2 10.1109/URAI.2013.6677409 List(http://dx.doi.org/10.1109/URAI.2013.6677409, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=6677409) 53e99967b7602d97021a5814 A signaling and control architecture for mobility support in wireless ATM networks 1 134 10.1007/BF01193262 List(http://dx.doi.org/10.1007/BF01193262, http://dx.doi.org/10.1109/ICC.1996.542243, http://dx.doi.org/https://doi.org/10.1007/BF01193262, https://link.springer.com/article/10.1007/BF01193262) 53e99967b7602d97021a581e DBDOC: querying and browsing databases and interrelated documents 3 10.1145/1557670.1557688 List(http://dx.doi.org/10.1145/1557670.1557688, http://doi.acm.org/10.1145/1557670.1557688) 53e99967b7602d97021a5680 Improving Learner Performance with Data Sampling and Boosting 1 8 10.1109/ICTAI.2008.58 List(http://dx.doi.org/10.1109/ICTAI.2008.58, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=4669723) 53e99960b7602d97021a546b To use PYA tool or not for learning Japanese hand alphabets 4 10.1145/1178823.1178884 List(http://dx.doi.org/10.1145/1178823.1178884, http://doi.acm.org/10.1145/1178823.1178884) 53e99960b7602d97021a546d On boolean functions with generalized cryptographic properties 2004 35 10.1007/978-3-540-30556-9_11 List(http://dx.doi.org/10.1007/978-3-540-30556-9_11, http://eprint.iacr.org/2004/259, http://www.webofknowledge.com/) 53e99967b7602d97021a5829 In-broker access control: towards efficient end-to-end performance of information brokerage systems 1 40 10.1109/SUTC.2006.1636183 List(http://dx.doi.org/10.1109/SUTC.2006.1636183, http://doi.ieeecomputersociety.org/10.1109/SUTC.2006.80, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=1636183) 53e99960b7602d97021a5470 A simulation study of TCP performance in ATM networks with ABR and UBR services 3 39 10.1109/INFCOM.1996.493073 List(http://dx.doi.org/10.1109/INFCOM.1996.493073, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=493073) 53e99960b7602d97

In [0]:
def check_return_data(check_type, data, cur):
    if data is not None and check_type in data:
        return data[check_type]
    else:
        return cur
    
def update_df(df, doi_list, data_list, data_str, is_int=False):
    data_dict = dict(zip(doi_list, data_list))
    update_data = udf(lambda x: data_dict[x], IntegerType() if is_int else StringType())
    return df.withColumn(data_str, update_data(F.col('doi')))

def get_publication_data(df):
    doi_list = df.select(F.col("doi")).rdd.flatMap(lambda x: x).collect()
    url_list = df.select(F.col("url")).rdd.flatMap(lambda x: x).collect()
    title_list = df.select(F.col("title")).rdd.flatMap(lambda x: x).collect()
    citation_list = df.select(F.col("n_citation")).rdd.flatMap(lambda x: x).collect()
    volume_list = df.select(F.col("volume")).rdd.flatMap(lambda x: x).collect()
    new_volume_list = []
    n_citation_list = []
    series_list = []
    new_doi_list = []
    for i, doi in enumerate(doi_list):
        try:
            if doi == "" or doi is None:
                if "doi" in url_list[i][0]:
                    doi_req = url_list[i][0].split("org/")[-1]
                else:
                    raise Exception
            else:
                doi_req = doi
            
            new_doi_list.append(doi_req)
            response = requests.get(f"https://api.crossref.org/works/{doi_req}")
            data = response.json()['message']
        except Exception:
            new_doi_list.append(None)
            data = None

        n_citation_list.append(int(check_return_data('is-referenced-by-count', data, citation_list[i])))
        new_volume_list.append(check_return_data('volume', data, volume_list[i]))
        temp = check_return_data('container-title', data, None)
        series_list.append(temp if temp == None or len(temp) < 1 else temp[0])

        time.sleep(0.05)
    
    df = update_df(df, doi_list, n_citation_list, 'n_citation')
    df = update_df(df, doi_list, new_volume_list, 'volume')
    df = update_df(df, doi_list, series_list, 'series')
    df = update_df(df, doi_list, new_doi_list, 'doi')
    
    return df

In [0]:
publications_raw = get_publication_data(publication_raw).filter("n_citation > 2")
# publication = get_publication_dataget_crossref_data(publication_raw).select("_id", "title", "volume", "series", "n_citation").filter("n_citation > 2")

publications = (publications_raw.select("title", "volume", "series", "n_citation")
            .dropDuplicates()
            .withColumn("publ_id", F.monotonically_increasing_id())
          )

publications = (publications_raw.join(publications, ["title", "volume", "series", "n_citation"])
           .select("publ_id", "title", "volume", "series", "n_citation")
           .dropDuplicates()
          )

display(publications)
publications.write.format("delta").mode("overwrite").saveAsTable("publications")

publ_id title volume series n_citation 322 THE BAYESIAN ABEL BOUND ON THE MEAN SQUARE ERROR 2006 IEEE International Conference on Acoustics Speed and Signal Processing Proceedings 13 192 MEBRS: a multiagent architecture for an experience based reasoning system 3681 Lecture Notes in Computer Science 4 497 Variable tapered pareto buffer design and implementation allowing run-time configuration for low-power embedded SRAMs 13 IEEE Transactions on Very Large Scale Integration (VLSI) Systems 20 556 An Object Observation for a Java Adaptative Distributed Application Platform Proceedings. International Conference on Parallel Computing in Electrical Engineering 12 138 Nash-Cournot Equilibria in Electric Power Markets with Piecewise Linear Demand Functions and Joint Constraints 55 Operations Research 136 359 Measurement and modeling of the origins of starvation of congestion-controlled flows in wireless mesh networks 17 IEEE/ACM Transactions on Networking 26 681 Intelligent preemption in construction of a manmade island for an airport Proceedings of the Winter Simulation Conference, 2005. 3 1 On Necessary and Sufficient Conditions for Private Ballot Submission. 184 Computer Physics Communications 9 81 Recursive square-root ladder estimation algorithms. 5 ICASSP '80. IEEE International Conference on Acoustics, Speech, and Signal Processing 40 98 Learning control of a parallel-link direct-drive robot manipulator 5 Robotics and Autonomous Systems 5 311 Comparison of the Efficiency of MapReduce and Bulk Synchronous Parallel Approaches to Large Network Processing 2012 IEEE 12th International Conference on Data Mining Workshops 12 403 Low Complexity Adaptive Turbo Frequency-Domain Channel Estimation for Single-Carrier Multi-User Detection 7 IEEE Transactions on Wireless Communications 10 671 Compressed Storage of Sparse Finite-State Transducers Lecture Notes in Computer Science 9 349 An experimental comparison of three rough set approaches to missing attribute values 6 Lecture Notes in Computer Science 17 516 Multivariate integration in weighted Hilbert spaces based on Walsh functions and weighted Sobolev spaces 21 Journal of Complexity 62 597 The complete proof on the economic order quantity under conditions of permissible delay in payments 59 Journal of the Operational Research Society 3 381 Containment of misinformation spread in online social networks Proceedings of the 4th Annual ACM Web Science Conference 121 206 RFID security in the context of "internet of things" Proceedings of the First International Conference on Security of Internet of Things 54 230 Convex sets of some doubly stochastic matrices 24 Journal of Combinatorial Theory, Series A 3 378 Energy-Efficient Neuron, Synapse and STDP Integrated Circuits. 6 IEEE Transactions on Biomedical Circuits and Systems 139 153 Robust spectral regression for face recognition 118 Neurocomputing 7 551 Automatical Adaption of the Stereotactical Coordinate System in Brain MRI Datasets Lecture Notes in Computer Science 11 609 Using redundancy to cope with failures in a delay tolerant network 35 ACM SIGCOMM Computer Communication Review 91 28 Intelligent tutoring system for CS-I and II laboratory Proceedings of the 44th annual Southeast regional conference 6 283 RF Tunable Bandstop Filters With Constant Bandwidth Based on a Doublet Configuration. 59 IEEE Transactions on Industrial Electronics 86 296 A Rewriting Logic Semantics for ATL. 184 Computer Physics Communications 9 434 A note on a problem concerning the axiomatic foundations of mereology. 4 Notre Dame Journal of Formal Logic 8 361 Avoiding Routing Loops on the Internet 36 Theory of Computing Systems 8 411 Can We Transform Requirements into Architecture? 2008 The Third International Conference on Software Engineering Advances 7 298 Combinatorial Structure of Schulte's Chiral Polyhedra 44 Discrete & Computational Geometry 11 525 Scale Invariant Face Detection Method Using Higher-Order Local Autocorrelation Features Extracted from Log-Polar

## Types

In [0]:
types_raw = filtered_df.limit(1000).select("_id", "volume", "issue", "doi", "url", "venue", "title")

display(types_raw)

_id volume issue doi url venue title 53e99967b7602d97021a560a 53 1 10.1007/s00453-007-9068-8 List(http://dx.doi.org/10.1007/s00453-007-9068-8, http://dx.doi.org/https://doi.org/10.1007/s00453-007-9068-8, https://link.springer.com/article/10.1007/s00453-007-9068-8, https://dl.acm.org/citation.cfm?id=3118965&picked=prox&preflayout=flat, http://www.webofknowledge.com/) List(539078f220f770854f5a882f, null, null, null, null, null, null, Algorithmica, null, null, null, null, 0) Consistent Sets of Secondary Structures in Proteins 53e99960b7602d97021a53fa 148 1-4 10.1016/S0020-0255(02)00276-1 List(http://dx.doi.org/10.1016/S0020-0255(02)00276-1, https://www.sciencedirect.com/science/article/pii/S0020025502002761) List(555036b77cea80f95414b7e3, null, null, null, null, null, null, Inf. Sci., null, null, null, null, 0) A new feature extraction technique for on-line recognition of handwritten alphanumeric characters 53e99960b7602d97021a5416 19 2 10.1093/llc/19.2.181 List(http://dx.doi.org/10.1093/llc/19.2.181) List(555036d37cea80f95415b0b3, null, null, null, null, null, null, LLC, null, null, null, null, 0) King John Divided 53e99960b7602d97021a541f 1 4 10.4018/jhcr.2010100102 List(http://dx.doi.org/10.4018/jhcr.2010100102, http://dx.doi.org/10.4018/978-1-4666-0921-1.ch017) List(555036cc7cea80f954158149, null, null, International Journal of Handheld Computing Research, null, null, null, IJHCR, null, null, null, null, 0) Peer Assist Live Streaming Overlay for Next-Generation-Networks 53e99960b7602d97021a5427 3222 10.1007/978-3-540-30141-7_67 List(http://dx.doi.org/10.1007/978-3-540-30141-7_67, http://www.webofknowledge.com/) List(null, 0302-9743, null, null, null, 1611-3349, null, LECTURE NOTES IN COMPUTER SCIENCE, null, LECTURE NOTES IN COMPUTER SCIENCE, null, J, null) Paramecium: Assembling Raw Nodes into Composite Cells 53e99967b7602d97021a5645 2 10.1109/IGARSS.2009.5418122 List(http://dx.doi.org/10.1109/IGARSS.2009.5418122, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=5418122) List(53a7297c20f7420be8bd4ae5, null, null, International Geoscience and Remote Sensing Symposium, null, null, null, IGARSS, null, null, null, null, 0) Radar Signal Retrodiffusion by Water Surface 53e99960b7602d97021a543e 10.1109/ICSMC.2008.4811630 List(http://dx.doi.org/10.1109/ICSMC.2008.4811630, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=4811630) List(555037277cea80f954176d3b, null, null, Systems, Man and Cybernetics, null, null, null, SMC, null, null, null, null, 0) Custos Remote on-demand healthcare aided with wireless sensors and mobile phones. 53e99967b7602d97021a566b 10.1109/ROBOT.2005.1570314 List(http://dx.doi.org/10.1109/ROBOT.2005.1570314) List(53a726bb20f7420be8b7f846, null, null, International Conference on Robotics and Automation, null, null, null, ICRA, null, null, null, null, 0) Group Elevator Scheduling with Advanced Traffic Information for Normal Operations and Coordinated Emergency Evacuation 53e99960b7602d97021a5451 10.1109/URAI.2013.6677409 List(http://dx.doi.org/10.1109/URAI.2013.6677409, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=6677409) List(555037017cea80f95416d334, null, null, International Conference on Ubiquitous Robots and Ambient Intelligence, null, null, null, URAI, null, null, null, null, 0) Weighted census transform for feature representation 53e99967b7602d97021a5814 1 3 10.1007/BF01193262 List(http://dx.doi.org/10.1007/BF01193262, http://dx.doi.org/10.1109/ICC.1996.542243, http://dx.doi.org/https://doi.org/10.1007/BF01193262, https://link.springer.com/article/10.1007/BF01193262) List(53a730a020f7420be8cff2d8, null, null, International Conference on Communications, null, null, null, MONET, null, null, null, null, 0) A signaling and control architecture for mobility support in wireless ATM networks 53e99967b7602d97021a581e 10.1145/1557670.1557688 List(http://dx.doi.org/10.1145/1557670.1557688, http://doi.acm.org/10.1145/1557670.1557688) List(53a72bfd20f7420be8c363ba, nul

In [0]:
types_pre_api = types_raw.withColumn("type", F.when(F.col("venue.raw").contains("@"), "workshop")
                   .when(((F.col("volume").isNotNull()) & (F.col("volume") != "")) | ((F.col("issue").isNotNull()) & (F.col("issue") != "")), "journal-article")
                   .otherwise("conference paper"))

display(types_pre_api)

_id volume issue doi url venue title type 53e99967b7602d97021a560a 53 1 10.1007/s00453-007-9068-8 List(http://dx.doi.org/10.1007/s00453-007-9068-8, http://dx.doi.org/https://doi.org/10.1007/s00453-007-9068-8, https://link.springer.com/article/10.1007/s00453-007-9068-8, https://dl.acm.org/citation.cfm?id=3118965&picked=prox&preflayout=flat, http://www.webofknowledge.com/) List(539078f220f770854f5a882f, null, null, null, null, null, null, Algorithmica, null, null, null, null, 0) Consistent Sets of Secondary Structures in Proteins journal-article 53e99960b7602d97021a53fa 148 1-4 10.1016/S0020-0255(02)00276-1 List(http://dx.doi.org/10.1016/S0020-0255(02)00276-1, https://www.sciencedirect.com/science/article/pii/S0020025502002761) List(555036b77cea80f95414b7e3, null, null, null, null, null, null, Inf. Sci., null, null, null, null, 0) A new feature extraction technique for on-line recognition of handwritten alphanumeric characters journal-article 53e99960b7602d97021a5416 19 2 10.1093/llc/19.2.181 List(http://dx.doi.org/10.1093/llc/19.2.181) List(555036d37cea80f95415b0b3, null, null, null, null, null, null, LLC, null, null, null, null, 0) King John Divided journal-article 53e99960b7602d97021a541f 1 4 10.4018/jhcr.2010100102 List(http://dx.doi.org/10.4018/jhcr.2010100102, http://dx.doi.org/10.4018/978-1-4666-0921-1.ch017) List(555036cc7cea80f954158149, null, null, International Journal of Handheld Computing Research, null, null, null, IJHCR, null, null, null, null, 0) Peer Assist Live Streaming Overlay for Next-Generation-Networks journal-article 53e99960b7602d97021a5427 3222 10.1007/978-3-540-30141-7_67 List(http://dx.doi.org/10.1007/978-3-540-30141-7_67, http://www.webofknowledge.com/) List(null, 0302-9743, null, null, null, 1611-3349, null, LECTURE NOTES IN COMPUTER SCIENCE, null, LECTURE NOTES IN COMPUTER SCIENCE, null, J, null) Paramecium: Assembling Raw Nodes into Composite Cells journal-article 53e99967b7602d97021a5645 2 10.1109/IGARSS.2009.5418122 List(http://dx.doi.org/10.1109/IGARSS.2009.5418122, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=5418122) List(53a7297c20f7420be8bd4ae5, null, null, International Geoscience and Remote Sensing Symposium, null, null, null, IGARSS, null, null, null, null, 0) Radar Signal Retrodiffusion by Water Surface journal-article 53e99960b7602d97021a543e 10.1109/ICSMC.2008.4811630 List(http://dx.doi.org/10.1109/ICSMC.2008.4811630, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=4811630) List(555037277cea80f954176d3b, null, null, Systems, Man and Cybernetics, null, null, null, SMC, null, null, null, null, 0) Custos Remote on-demand healthcare aided with wireless sensors and mobile phones. conference paper 53e99967b7602d97021a566b 10.1109/ROBOT.2005.1570314 List(http://dx.doi.org/10.1109/ROBOT.2005.1570314) List(53a726bb20f7420be8b7f846, null, null, International Conference on Robotics and Automation, null, null, null, ICRA, null, null, null, null, 0) Group Elevator Scheduling with Advanced Traffic Information for Normal Operations and Coordinated Emergency Evacuation conference paper 53e99960b7602d97021a5451 10.1109/URAI.2013.6677409 List(http://dx.doi.org/10.1109/URAI.2013.6677409, http://ieeexplore.ieee.org/xpl/abstractAuthors.jsp?tp=&arnumber=6677409) List(555037017cea80f95416d334, null, null, International Conference on Ubiquitous Robots and Ambient Intelligence, null, null, null, URAI, null, null, null, null, 0) Weighted census transform for feature representation conference paper 53e99967b7602d97021a5814 1 3 10.1007/BF01193262 List(http://dx.doi.org/10.1007/BF01193262, http://dx.doi.org/10.1109/ICC.1996.542243, http://dx.doi.org/https://doi.org/10.1007/BF01193262, https://link.springer.com/article/10.1007/BF01193262) List(53a730a020f7420be8cff2d8, null, null, International Conference on Communications, null, null, null, MONET, null, null, null, null, 0) A signaling and control architecture for mobility support in wireless ATM networks journal-article 53e9996

In [0]:
def check_return_data(check_type, data, cur):
    if data is not None and check_type in data:
        return data[check_type]
    else:
        return cur
    
def update_df(df, doi_list, data_list, data_str, is_int=False):
    new_df = spark.createDataFrame(zip(df.select("doi").rdd.flatMap(lambda x: x).collect(), data_list), ["doi", data_str])
    return df.join(new_df, on="doi", how="left").select(new_df["doi"], new_df[data_str], F.col("title"))

def get_type_data(df):
    doi_list = df.select(F.col("doi")).rdd.flatMap(lambda x: x).collect()
    url_list = df.select(F.col("url")).rdd.flatMap(lambda x: x).collect()
    type_list = df.select(F.col("type")).rdd.flatMap(lambda x: x).collect()
    new_type_list = []
    for i, doi in enumerate(doi_list):
        try:
            if doi == "" or doi is None:
                if "doi" in url_list[i][0]:
                    doi_req = url_list[i][0].split("org/")[-1]
                else:
                    raise Exception
            else:
                doi_req = doi
            
            response = requests.get(f"https://api.crossref.org/works/{doi_req}")
            data = response.json()['message']
        except Exception:
            data = None

        new_type_list.append(check_return_data('type', data, type_list[i]))

        time.sleep(0.05)

    df = update_df(df, doi_list, new_type_list, 'type')
    
    return df

In [0]:
types_raw = get_type_data(types_pre_api)

types = (types_raw.select("type")
            .dropDuplicates()
            .withColumn("type_id", F.monotonically_increasing_id())
          )

types = (types_raw.join(types, ["type"])
           .select("type_id", "type", "title")
           .dropDuplicates()
        )

display(types)

types_clean = types.select("type_id", "type")
types_clean.write.format("delta").mode("overwrite").saveAsTable("types")

type_id type title 6 book Logic for Programming, Artificial Intelligence, and Reasoning, 9th International Conference, LPAR 2002, Tbilisi, Georgia, October 14-18, 2002, Proceedings 6 book eCall: Automatic notification of a road traffic accident. 6 book Buffer Overflows und Format-String-Schwachstellen - Funktionsweisen, Exploits und Gegenmaßnahmen 6 book Current-Reused QVCO Based on Source-Connection Coupling. 6 book Effective information sharing using update logs 6 book Security Issues in Health Care Process Integration ? a Research-in-Progress Report 6 book A Social Cognitive View of Technical Support and its Influence on User Learning. 6 book Eine integrierte Softwarelösung zur konsolidierten Rechnungslegung 6 book How to Select Significant Workloads in Performance Models 6 book Selection of the most effective set of subword units for an HMM-based speech recognition system 6 book The Transient Behaviour of Networks with Infinite Server Nodes 6 book Analysis of Mixed Natural and Symbolic Input in Mathematical Dialogs 6 book Sensor network localisation with wrapped phase measurements. 6 book Code Museums as Functional Tests for Static Analyses. 6 book Learning by demonstration in repeated stochastic games 6 book Planning under temporal uncertainty indurative actions 6 book -D Face Point Trajectory Synthesis Using An Automatically Derived Visual Phoneme Similarity Matrix 6 book Network Applications of Bloom Filters: A Survey 6 book Self-Learning for Player Localization in Sports Video. 6 book The New Object-Relational Generation and its Application in Web Databases 6 book Task Model Representation of a Collaborative System using Hypermedia Networks. 6 book Using Design Patterns, Frameworks and CORBA to Reduce the Complexity of Developing Reusable Large-Scale Object-Oriented Concurrent Communication Components and Systems 6 book End-To-End Delay Modeling for Mobile Ad Hoc Networks: A Quasi-Birth-and-Death Approach. 6 book Adaptive query processing: Why, How, When, and What Next? 6 book Exploring initiative strategies using computer simulation 6 book Computing with Unreliable Information (Preliminary Version) 6 book Collaborative peer to peer edition: Avoiding conflicts is better than solving conflicts 6 book Parallel non-linear dimension reduction algorithm on GPU. 6 book Incorporating Software Visualization into Prolog Teaching: A Challenge, a Restriction and an Opportunity 6 book Embedded Cantonese TTS for multi-device access to web content 6 book Qualitative Modelling via Constraint Programming: Past, Present and Future 6 book Comparative Study of Profiled School Scheduling Programs in Lithuania 6 book Dynamic map: representation of interactions between robots 6 book Symbol Creator: An Alternative Eye-based Text Entry Technique with Low Demand for Screen Space 6 book The Effect of Information Retrieval Method Using Dependency Relationship Between Words 6 book Extreme Programming (XP) as a Development Process Framework 6 book Another Algorithm Determining the Independence Number of a Graph 6 book Genetic Programming: An emerging engineering tool 6 book Utilizing Displayless Space in Collocated Games 6 book Transparent Integration of Continuous Media Support into a Multimedia DBMS 6 book A Web Services Based Streaming Gateway for Heterogeneous A/V Collaboration 6 book Unsupervised Learning of Bayesian Networks Via Estimation of Distribution Algorithms 6 book ePortfolio implementation strategy of FH JOANNEUM 6 book On bent functions with zero second derivatives. 6 book MASCOTS '93, Proceedings of the International Workshop on Modeling, Analysis, and Simulation On Computer and Telecommunication Systems, January 17-20, 1993, La Jolla, San Diego, CA, USA 6 book A probabilistic neural network approach to jet engine fault diagnosis 6 book A Multimodal Approach to Bridge the Music Semantic Gap 6 book Online-estimation of road map elements using spline curves. 6 book Reverse-engineering drivers for safety and portability 6 book An uns

## Keywords

In [0]:
keywords_raw = filtered_df.limit(1000).select("_id", "keywords", "doi", "title")

display(keywords_raw)

_id keywords doi title 53e99967b7602d97021a560a List(Secondary Structure, Maximum Weight, Local Prediction, Horizontal Edge, Connector Edge) 10.1007/s00453-007-9068-8 Consistent Sets of Secondary Structures in Proteins 53e99960b7602d97021a53fa List(adaptive on-line use, data processing system, feature extraction, inputting data, on-line recognition, handwritten alphanumeric character, feature set, new feature extraction technique, extracted feature, adaptive recognizer, new method, high generalization capability, high recognition rate, feed forward neural network, error back propagation, simulation experiment, data processing, artificial neural network) 10.1016/S0020-0255(02)00276-1 A new feature extraction technique for on-line recognition of handwritten alphanumeric characters 53e99960b7602d97021a5416 List() 10.1093/llc/19.2.181 King John Divided 53e99960b7602d97021a541f List(scalability, ims, p2p, ngn, next generation network) 10.4018/jhcr.2010100102 Peer Assist Live Streaming Overlay for Next-Generation-Networks 53e99960b7602d97021a5427 List() 10.1007/978-3-540-30141-7_67 Paramecium: Assembling Raw Nodes into Composite Cells 53e99967b7602d97021a5645 List(airborne radar, backscatter, height measurement, oceanographic regions, oceanographic techniques, remote sensing by radar, synthetic aperture radar, Camargue region, DRIVE radar, France, ONERA BUSARD platform, SAR instrument, backscattering coefficient profiles, dry surfaces, future space Ka band altimetry missions, nadir backscattering, pond surfaces, sea surfaces, sensor configuration, specular behavior, steep radar incident angle, synthetic aperture radar, water surface radar signal retrodiffusion, wet surfaces, Ka band, altimetry mode, radar sensor) 10.1109/IGARSS.2009.5418122 Radar Signal Retrodiffusion by Water Surface 53e99960b7602d97021a543e List(Java, Web services, biomedical telemetry, health care, mobile computing, sensor fusion, telemedicine, wireless sensor networks, Custos, ICT technique, Internet, Squawk Java J2ME, Sun SPOT, UPnP digital-home platform, Web service, Wei-Gong memorial hospital, clinical trial, geriatric psychiatry ward, mobile phone, multisensor data fusion, remote on-demand healthcare, small programmable object technology, smart phone, wireless sensor network, Smart Environments, Telemedicine, Telemonitoring, Wireless Sensor Networks) 10.1109/ICSMC.2008.4811630 Custos Remote on-demand healthcare aided with wireless sensors and mobile phones. 53e99967b7602d97021a566b List(information technology, simulation, transportation, objective function, dynamic programming, state space, sensor network, elevators, uncertainty, testing, normal operator, look ahead, lagrangian relaxation, local search) 10.1109/ROBOT.2005.1570314 Group Elevator Scheduling with Advanced Traffic Information for Normal Operations and Coordinated Emergency Evacuation 53e99960b7602d97021a5451 List(weighted census transform, visual feature representation method, image representation, binary code bit, face recognition, ar face datasets, modified census transform, wct, statistical analysis, feature representation model, visual image classification, feature representation, training dataset, compressed sensing, image classification, statistical approach, mct, entropy information, transforms, entropy, compressive sensing technique, pattern classification) 10.1109/URAI.2013.6677409 Weighted census transform for feature representation 53e99967b7602d97021a5814 List(Wireless Link, Mobile Terminal, Control Protocol, Control Architecture, Control Layer) 10.1007/BF01193262 A signaling and control architecture for mobility support in wireless ATM networks 53e99967b7602d97021a581e List(user-defined functions, typical database schema, document-to-metadata link, different level, interrelated document, typical information retrieval capability, sql code generation, browsing databases, large collection, acceptable performance, basic set, information retrieval, xml, code generation) 10.1145/1557670.1

In [0]:
# Load the spaCy model
nlp = spacy.load("en_core_web_sm")

def is_city_location_person(keyword):
    # Process the keyword using the spaCy NER model
    doc = nlp(keyword)
    
    # Check if any of the entities recognized by the model are of type GPE (city or location) or PERSON
    for ent in doc.ents:
        if ent.label_ in ['GPE', 'PERSON']:
            return True
    
    return False

def update_df(df, doi_list, data_list, data_str, is_int=False):
    data_dict = dict(zip(doi_list, data_list))
    update_data = udf(lambda x: data_dict[x], IntegerType() if is_int else StringType())
    return df.withColumn(data_str, update_data(F.col('doi')))

def check_keywords(df):
    doi_list = df.select(F.col("doi")).rdd.flatMap(lambda x: x).collect()
    keywords_list = df.select(F.col("keywords")).rdd.flatMap(lambda x: x).collect()
    new_keywords_list = []
    for i, keys in enumerate(keywords_list):
        temp = []
        for k in keys:
            if not is_city_location_person(k):
                temp.append(k)
        new_keywords_list.append(temp)
        
    df = update_df(df, doi_list, keywords_list, 'keywords')
    
    return df

In [0]:
keywords_raw = check_keywords(keywords_raw).filter(F.size(keywords_raw.keywords) > 0)


keywords = (keywords_raw.select("keywords")
            .dropDuplicates()
            .withColumn("keyw_id", F.monotonically_increasing_id())
          )

keywords = (keywords_raw.join(keywords, ["keywords"])
           .select("keyw_id", "keywords", "title")
           .dropDuplicates()
        )

display(keywords)

keywords_clean = keywords.select("keyw_id", "keywords")
keywords_clean.write.format("delta").mode("overwrite").saveAsTable("keywords")

keyw_id keywords title 0 [speaker model, multiple session, large data, large data set, incremental robust adaptation method, incremental adaptation method, inaccurate speaker model, robust speaker recognition, large amount, utterance variation, speaker recognition system, incremental verstion, speaker recognition, gaussian mixture model] Robust speaker recognition against utterance variations 1 [asymptotic behavior, constant coefficient, rational difference equation, phase portrait, rational type difference equation, attractor, phase space] On the asymptotic behavior of a system of two rational difference equations 2 [Insurance, Greece, Productivity change, Bootstrapped DEA] Efficiency in the Greek insurance industry 3 [graph isomorphism, 3-connected graph, linear time algorithm, map isomorphism, planar graph, whitney equivalence, graph g, fixed surface, linear time, polyhedral embeddings, embedded graph, time complexity, connected graph] Graph and map isomorphism and all polyhedral embeddings in linear time 4 [keystroke-level model, keystroke-level model prediction, observed data, investigative step, handheld device, total duration, aggregated event, cognitive modeling research, klm mental preparation duration, human-computer interaction, model prediction, cognitive modeling, keystroke level model, cognitive model, human computer interaction] Comparisons of keystroke-level model predictions to observed data 5 [automated office environment, alpha beta search] Ergonmics in the automated office environment. 6 [Bayes methods, IEEE standards, Monte Carlo methods, maximum likelihood estimation, optimisation, protocols, state estimation, wireless LAN, Bayesian estimators, DCF, IEEE 802.11 protocol, MAP estimation, approximate maximum a posteriori estimation, backoff parameters, competing terminals, distributed coordination function, network state, ns-2 simulator, optimization mechanisms, predictive distribution, saturation mode, sequential Monte Carlo estimation] OPTIMIZING IEEE 802.11 DCF USING BAYESIAN ESTIMATORS OF THE NETWORK STATE 7 [error detection strategy, cognitive impairment, important contribution, users age, error detection, internet user, critical factor, modern society, older adults, present study, improving web accessibility, older adult, service provider, usability, internet, servers, color, web accessibility, quality of life, web pages, data mining] Using an Error Detection Strategy for Improving Web Accessibility for Older Adults 8 [word group, general constraint solver, local word, integer programming problem, important novel feature, lexicalised grammar formalism, finite state machine specification, fast grouper, indian language, karaka role, machine translation, finite state machine] A karaka based approach to parsing of Indian languages 9 [measurement error, spectrum, dead reckoning] Cooperative Localization in GPS-Limited Urban Environments 10 [Complexity theory, Decoding, Turbo codes, Bit error rate, Measurement, Convolutional codes, Systematics] Turbo Decoding Using the Sectionalized Minimal Trellis of the Constituent Code: Performance-Complexity Trade-Off. 11 [sparse paving matroids, large class, basis-exchange property, basis-exchange conjecture, matroid] Basis-exchange properties of sparse paving matroids 12 [satisfiability] Bargaining over multiple issues with maximin and leximin preferences 13 [search, constraint satisfaction, mathematical foundations, phase transition, constraint satisfaction problem, search space] Inherent Choice in the Search Space of Constraint Satisfaction Problem Instances 14 [gaussian pyramid, image fusion, laplacian pyramid, multi-focus image] A Multi-focus Image Fusion Method Based on Laplacian Pyramid. 15 [project management., software qual- ity, project risk management, software project risk management, software engineering, risk analysis, risk management] Enhancements in Software Project Risk Management 16 [health, broad agendum, tangible design outcome, design idea, cscw co

## Venue

In [0]:
# https://pypi.org/project/habanero/
from habanero import Crossref
cr = Crossref()

def getVenue(doi, venue):
    result = [venue['name_d'], None]
    try:
        query = cr.works(ids = doi)['message']['event']
        result[0] = query['name']
        result[1] = query['location']
    except:
        pass
    return result

getVenueUDF = udf(getVenue, ArrayType(StringType()))

In [0]:
venues_df = (filtered_df
            .limit(1000)
            .select('title', "doi", 'venue')
            .withColumn("VENUE", getVenueUDF(F.col("doi"), F.col('venue')))
            .select('title',
                    F.col("VENUE")[0].alias("venue"),
                    F.col("VENUE")[1].alias("location")
                   )
             .dropna(subset="venue")
           )

venues = (venues_df.select("venue", "location")
            .dropDuplicates()
            .withColumn("venue_id", F.monotonically_increasing_id())
          )

venues = (venues_df.join(venues, ["venue", "location"])
           .select("venue_id", "venue", "location", "title")
           .dropDuplicates()
        )

display(venues)
venues_clean = venues.select("venue_id", "venue")
venues_clean.write.format("delta").mode("overwrite").saveAsTable("venues")

venue_id venue location title 67 2012 IEEE 12th International Conference on Data Mining Workshops Brussels, Belgium Comparison of the Efficiency of MapReduce and Bulk Synchronous Parallel Approaches to Large Network Processing 88 2009 IEEE 69th Vehicular Technology Conference Barcelona Energy Consumption Optimization for Data Collection with Precision Constraints in Wireless Sensor Networks 489 ACM SE06: ACM Southeast Regional Conference Melbourne Florida Density-based multipath secure communication over mobile ad hoc networks 145 the ACM SIGCSE-SIGCUE technical symposium Not Known Learning mathematics with recursive computer programs 279 Second IEEE and ACM International Symposium on Mixed and Augmented Reality Tokyo, Japan Real-Time Localisation and Mapping with Wearable Active Vision 229 First International Conference on Innovative Computing, Information and Control - Volume I (ICICIC'06) Beijing, China Numerical Analysis of Blood Flow in Vessels 404 1995 IEEE International Conference on Robotics and Automation Nagoya, Japan Robot manipulator contact force control application of fuzzy-neural network 185 2009 IEEE International Workshop on Genomic Signal Processing and Statistics (GENSIPS) Minneapolis, MN, USA On the Mutual Information Between Interaction Perplexity and Function of Proteins 290 2008 19th International Conference on Pattern Recognition (ICPR) Tampa, FL, USA 3D localization of partially buried object in unstructured environment 484 2009 IEEE International Geoscience and Remote Sensing Symposium Cape Town, South Africa Radar Signal Retrodiffusion by Water Surface 175 Seventh IEEE International Symposium on Cluster Computing and the Grid (CCGrid '07) Rio De Janeiro A Robust Decentralized Job Scheduling Approach for Mobile Peers in Ad-hoc Grids 461 2013 ACM/IEEE International Symposium on Empirical Software Engineering and Measurement (ESEM) Baltimore, Maryland Impact of Triage: A Study of Mozilla and Gnome 197 the 1981 conference Portsmouth, New Hampshire, United States A relational language for parallel programming 115 2012 IEEE International Conference on Development and Learning and Epigenetic Robotics (ICDL) San Diego, CA, USA Active robot learning with human tutelage. 134 2006 IEEE International Conference on Communications Istanbul Uncoordinated Distributed Space-Time Trellis Coding. 3 the 12th conference Budapest, Hungry Massive disambiguation of large text corpora with flexible categorial grammar 338 1994 International Conference on Parallel and Distributed Systems Hsinchu, Taiwan Experiences in session layer conformance testing 177 Proceedings of the IEEE 2004 Custom Integrated Circuits Conference Orlando, FL, USA A Low-voltage Low-power Sigma-delta Modulator with Improved Performance in Overload Condition 204 HotNets-XI: 11th ACM Workshop on Hot Topics in Networks Redmond Washington Software-defined internet architecture: decoupling architecture from infrastructure 139 IGARSS 2011 - 2011 IEEE International Geoscience and Remote Sensing Symposium Vancouver, BC, Canada Analysis of active and passive microwave observations from the NoSREx campaign. 141 the 6th annual international conference Ann Arbor, Michigan, United States Bridging the moat: helping training and documentation to work together 285 Proceedings of 26th Annual International Symposium on Microarchitecture (Cat. No.93TH0602-3) Austin, TX, USA Prophetic branches: a branch architecture for code compaction and efficient execution 106 2013 6th Joint IFIP Wireless and Mobile Networking Conference (WMNC 2013) Dubai Level-based on-demand multicast routing protocol for mobile Ad Hoc networks. 162 the 28th conference San Francisco, California, United States A unified approach to input-output encoding for FSM state assignment 13 2010 IEEE International Conference on Wireless Communications, Networking and Information Security (WCNIS) Beijing, China Multiple beams scanning double square loop antenna for UWB communications. 135 MM09: ACM Multimedia Conf

## FieldOfStudy

In [0]:
def getFos(doi, fos):
    result = [] if not fos else fos
    query = []
    try:
        query = cr.works(ids = doi)['message']['subject']
    except:
        pass
    return [*result, *query]

getFosUDF = udf(getFos, ArrayType(StringType()))

In [0]:
fos_df = (filtered_df
          .limit(1000)
          .select('title', "doi", 'fos')
          .withColumn("FOS", getFosUDF(F.col("doi"), F.col("fos")))
          .select('title', F.col('FOS').alias('fos'))
          .filter(F.size('fos') > 0)
           )

fos = (fos_df.select("fos")
            .dropDuplicates()
            .withColumn("fos_id", F.monotonically_increasing_id())
          )

fos = (fos_df.join(fos, ["fos"])
           .select("fos_id", "fos", "title")
           .dropDuplicates()
        )

display(fos)
fos_clean = fos.select("fos_id", "fos")
fos_clean.write.format("delta").mode("overwrite").saveAsTable("fos")

fos_id fos title 0 List(Penetration (firestop), Uniqueness, Water sorption, Starch gelatinization, Swelling, Mechanics, Nonlinear integral equation, Materials science, Technical literature, Applied Mathematics, Computer Science Applications, General Engineering, Statistics and Probability, Applied Mathematics, Computer Science Applications, General Engineering, Statistics and Probability) A mathematical model for spaghetti cooking with free boundaries. 1 List(Video server, Broadcasting, Fast Ethernet, Lifting equipment, Computer science, Scheduling (computing), Computer network, Workstation, Customer base, Scalability) Tabbycat: an inexpensive scalable server for video-on-demand. 2 List(Computer software, Software engineering, Computer science, Empirical process (process control model), Software maintenance, Replicate) Replication's Role in Software Engineering 3 List(Swap (computer programming), Return time, Program transformation, Functional programming, Inversion (meteorology), Computer science, Theoretical computer science, Swap (finance), Computation, Software) Manipulating accumulative functions by swapping call-time and return-time computations* 4 List(Programming language, Computer science, Extreme programming) Extreme Programming (XP) as a Development Process Framework 5 List(Graph theory, Discrete mathematics, Two-way deterministic finite automaton, Deterministic automaton, Finite-state machine, Finite graph, Mathematics, Monad (functional programming)) Recognizability Equals Definability for Partial k-Paths 6 List(Metadata, Computer aided instruction, Computer science, Rights Expression Language, Distance education, Learning object, Human–computer interaction, Artificial intelligence, Granularity, Intellectual property, Industrial property) Research on DRM-enabled learning objects model 7 List(Financial economics, Insurance industry, Economics, Simar, Actuarial science, Open market operation, Ranking, Deregulation, Productivity change, Data envelopment analysis, Market share, Information Systems and Management, Management Science and Operations Research, Modeling and Simulation, General Computer Science, Industrial and Manufacturing Engineering) Efficiency in the Greek insurance industry 8 List(Wireless network, Key distribution in wireless sensor networks, Computer science, Computer network, Network simulation, Wireless WAN, Wi-Fi array, Heterogeneous network, Municipal wireless network, Wireless sensor network) Evaluation of Cognitive Wireless Networks in Rural Area for Disaster Information Network 9 List(Health care, Telemedicine, Population, Gerontology, Competence (human resources), Elderly population, Norm (social), Medicine, Ageing society, Health clinic) Applicability of Portable Health Clinic to Ageing Society. 10 List(Buffer (optical fiber), Telecommunications network, Computer science, Computer network, Communication channel, Default gateway, Local area network, Throughput, Computation, Distributed computing, Computer Networks and Communications) Gateway performance analysis in interconnected networks 11 List(Computer science, Computer network, Orthogonal frequency-division multiple access, WiMAX, Resource allocation, Mapping algorithm, System model, Voice over IP, Computational complexity theory, Electrical and Electronic Engineering, Computer Networks and Communications, Information Systems) Efficient mapping of multiple VoIP vocoders in WiMAX systems 12 List(Computer science, Distributed computing) Computing with Unreliable Information (Preliminary Version) 13 List(Information structure, Authentication, Decision support system, Commerce, Regulatory competition, User requirements document, E-commerce, Business, Management of Technology and Innovation, Computer Science Applications) U.S. and EU Regulatory Competition and Authentication Standards in Electronic Commerce 14 List(Remotely operated underwater vehicle, Computer vision, Visual odometry, Photomapping, Computer science, Robustness (computer scien

## Date

In [0]:
def getDate(doi, year):
    formated = [None, None, None]
    try:
        query = cr.works(ids = doi)['message']['issued']['date-parts'][0]
        for i in [0, 1, 2]:
            formated[i] = query[i]
    except:
        pass
    if formated[0] == None:
        formated[0] = year 
    return formated

getDateUDF = udf(getDate, ArrayType(StringType()))

In [0]:
dates_df = (filtered_df
            .limit(1000)
            .select('title', "year", "doi")
            .withColumn("Date", getDateUDF(F.col("doi"), F.col("year")))
            .select('title',
                    F.col("Date")[2].alias("day"),
                    F.col("Date")[1].alias("month"),
                    F.col("Date")[0].alias("year")
                   )
           )

dates = (dates_df.select([F.col("day").alias("day1"), F.col("month").alias("month1"), F.col("year").alias("year1")])
            .dropDuplicates()
            .withColumn("date_id", F.monotonically_increasing_id())
          )

dates = (dates_df.join(dates, ((dates_df.day.eqNullSafe(dates.day1)) & 
                               (dates_df.month.eqNullSafe(dates.month1)) &
                               (dates_df.year.eqNullSafe(dates.year1))))
           .select("date_id", "day", "month", "year", "title")
           .dropDuplicates()
        )

display(dates)

dates_clean = dates.select("date_id", "day", "month", "year")
dates_clean.write.format("delta").mode("overwrite").saveAsTable("dates")

date_id day month year title 0 10 11 2007 Consistent Sets of Secondary Structures in Proteins 1 null 12 2002 A new feature extraction technique for on-line recognition of handwritten alphanumeric characters 2 1 6 2004 King John Divided 3 1 10 2010 Peer Assist Live Streaming Overlay for Next-Generation-Networks 4 null null 2004 Paramecium: Assembling Raw Nodes into Composite Cells 5 null null 2009 Radar Signal Retrodiffusion by Water Surface 6 null 10 2008 Custos Remote on-demand healthcare aided with wireless sensors and mobile phones. 7 null null 2005 Group Elevator Scheduling with Advanced Traffic Information for Normal Operations and Coordinated Emergency Evacuation 8 null 10 2013 Weighted census transform for feature representation 9 null 10 1996 A signaling and control architecture for mobility support in wireless ATM networks 10 28 6 2009 DBDOC: querying and browsing databases and interrelated documents 11 null 11 2008 Improving Learner Performance with Data Sampling and Boosting 12 14 6 2006 To use PYA tool or not for learning Japanese hand alphabets 4 null null 2004 On boolean functions with generalized cryptographic properties 13 null null 2006 In-broker access control: towards efficient end-to-end performance of information brokerage systems 14 null null 1996 A simulation study of TCP performance in ATM networks with ABR and UBR services 7 null null 2005 Comparative Study of Sequential Pattern Mining Models 15 null null 1994 Reference Resolution Using Semantic Patterns in Japanese Newspaper Articles. 16 1 6 2015 Secure and scalable match: overcoming the universal circuit bottleneck using group programs. 17 null null 2000 User profiling with Case-Based Reasoning and Bayesian Networks 18 null null 1999 TOOLS 1999: 31st International Conference on Technology of Object-Oriented Languages and Systems, 22-25 September 1999, Nanjing, China 19 10 2 2011 Algorithm-level error detection for Montgomery ladder-based ECSM 20 null null 2007 The Open Document Format and its Impact on Accessibility for Persons with a Reading Impairment 21 null null 1993 Undecidability of the Surjectivity Problem for 2D Cellular Automata: A Simplified Proof 22 null 3 2001 Rent's rule based switching requirements 13 null null 2006 A Regular Layout Approach for ASICs 23 null null 2003 Extreme Programming and Agile Processes in Software Engineering, 4th International Conference, XP 2003, Genova, Italy, May 25-29, 2003 Proceedings 24 null null 2002 A Realistic Look At Failure Detectors 25 null 6 2013 Dynamic Logic of Propositional Assignments: A Well-Behaved Variant of PDL 20 null null 2007 A distributed virtual reality-based system for neonatal decision-making training 17 null null 2000 Planning under uncertainty via stochastic satisfiability 26 null 8 2008 The complete proof on the economic order quantity under conditions of permissible delay in payments 27 null 7 2005 Designing IIR filters with a given 3-dB point 17 null null 2000 The Role of Process in a Software Start-up 23 null null 2003 Control Algorithm for 6-Primary Displays Minimizing Effects of Observer Metamerism 28 null 7 2010 Design and development of Digital Movie Guide service for approaching Community Coordinated Multimedia 23 null null 2003 Collaborative Work Tools in Learning Environments 7 null null 2005 Research on DRM-enabled learning objects model 29 null 3 2011 A hybrid fem-based method for aligning prone and supine images for image guided breast surgery 7 null null 2005 Parallel Consistency Maintenance of Materialized Views Using Referential Integrity Constraints in Data Warehouses 30 null null 1983 A trellis code construction and coding theorem for stationary Gaussian sources 31 null 8 2011 Design and realization of DICOM/HL7 gateway in PACS 32 null 4 2004 Computation of the finitistic dimension of monomial algebras 33 null 9 2001 Local lifetime control IGBT structures: turn-off performances comparison for hard- and soft-switching between 1200V trench and new planar PT-IGBTs. 34

## Language

In [0]:
display(raw_df.groupBy("lang").count())
display(filtered_df.groupBy("lang").count())

lang count en 249984 zh 16

lang count en 244930

In [0]:
lang_df = filtered_df.select("title", "lang")

lang = (lang_df.select("lang")
            .dropDuplicates()
            .withColumn("lang_id", F.monotonically_increasing_id())
          )

lang = (lang_df.join(lang, ["lang"])
           .select("lang_id", "lang", "title")
           .dropDuplicates()
        )

display(lang)

lang_clean = lang.select("lang_id", "lang")
lang_clean.write.format("delta").mode("overwrite").saveAsTable("lang")

lang_id lang title 0 en An adaptive technique for content-based image retrieval 0 en Controlling Self-Organising Software Applications with Archetypes 0 en Non-Automatizability of Bounded-Depth Frege Proofs 0 en Buffer Overflows und Format-String-Schwachstellen - Funktionsweisen, Exploits und Gegenmaßnahmen 0 en Empowering iso-surfaces with volume data 0 en Partitioning and Retiming of Multi-Dimensional Systems 0 en A Comparison Between Contour Elevation Data Sources for DEM Creation and Soil Carbon Prediction, Coshocton, Ohio 0 en A pairing-based publicly verifiable secret sharing scheme. 0 en A relational model for unstructured documents 0 en A survey on applications of the harmony search algorithm. 0 en Relaxation of a Control Problem in the Coefficients with a Functional of Quadratic Growth in the Gradient 0 en Gaussian Process Bandits for Tree Search 0 en Association Rule Mining of Relational Data 0 en Visualizing vector fields: the thick oriented stream-line algorithm (TOSL) 0 en Detection of spatiotemporal phase patterns in ECoG using adaptive mixture models. 0 en Towards an Ontology for Knowledge Organisation in the Field of eGovernment 0 en Varying Density Spatial Clustering Based on a Hierarchical Tree 0 en LexTec ― a rich language resource for technical domains in Portuguese. 0 en Route Search over Probabilistic Geospatial Data 0 en A Distributed Mutual Exclusion Algorithm for Mobile Ad-Hoc Networks 0 en Parameter estimation for two synthetic gene networks: a case study. 0 en The mu VP 64-bit vector coprocessor: a new implementation of high-performance numerical computation 0 en Adjustable Width Linear Combinational Scan Vector Decompression 0 en Efficient virtual reality design of quiet underwater shells 0 en Developing user interface guidelines for DVD menus 0 en Reconfigurable Signal Processing in Wireless Terminals 0 en Zur Automatischen Ermittlung von Testszenarien aus EPK-Schemata 0 en Detecting pruning of individual stems using Airborne Laser Scanning data captured from an Unmanned Aerial Vehicle. 0 en Formal Synthesis and Control of Soft Embedded Real-Time Systems 0 en SKY:Efficient peer-to-peer networks based on distributed Kautz graphs 0 en Leak monitoring system for gas pipelines 0 en Commemorating William Playfair’s 250th birthday 0 en Crank-Nicolson difference scheme for the coupled nonlinear Schrödinger equations with the Riesz space fractional derivative 0 en An Averaging Technique for Highly Oscillatory Hamiltonian Problems 0 en Inverting X: An Architecture for a Shared Distributed Window System 0 en Complete and non-overlapping marching along a closed regular intersection curve 0 en Scene-based non-uniformity correction: From algorithm to implementation on a smart camera 0 en Traffic Condition Is More Than Colored Lines on a Map: Characterization of Waze Alerts 0 en Data Management in eCommerce: The Good, the Bad, and the Ugly 0 en A group multicast routing algorithm by using multiple minimum Steiner trees 0 en Weighted LAD-LASSO method for robust parameter estimation and variable selection in regression 0 en A Workflow Management Systems Architecture that Support Ad-Hoc Recoveries 0 en Conquering the Storage Pyramid - Implementing the Dynamic Library 0 en Data-driven neighborhood selection of a Gaussian field 0 en Performance Evaluation of Vision-Based Real-Time Motion Capture 0 en Coping with Stress Tests: Managing the Application Benchmark 0 en Debug Support for Scalable System-on-Chip 0 en Two-level pattern recognition in a class of knowledge-based systems 0 en A Communication Middleware for Mobile and Ad-hoc Senarios 0 en A pattern matching compiler for multiple target languages 0 en 12th European Meeting on Cybernetics And Systems Research. 0 en Research on Risk in Long-Term Reservoir Dynamic Probability Scheduling 0 en Comparative analysis of power yield improvement under process variation of sub-threshold flip-flops 0 en Enterprise Integration via CORBA-Based Information Agents 0 en Reconfig

## MAIN TABLE

In [0]:
main_table = (publications.join(authors, ["title"])
              .join(organization, ["author"], "left")
              .join(types, ["title"])
              .join(keywords, ["title"])
              .join(venues, ["title"])
              .join(fos, ["title"])
              .join(dates, ["title"])
              .join(lang, ["title"])
              .select("publ_id", "author_id", "org_id", "type_id", "keyw_id", "venue_id", "fos_id", "date_id", "lang_id", F.col("rank").alias("author_rank"))
              )
display(main_table)
main_table.write.format("delta").mode("overwrite").option("overwriteSchema", "true").saveAsTable("DBLP_fact_table")

publ_id author_id org_id type_id keyw_id venue_id fos_id date_id lang_id author_rank 440 36 null 2 404 307 1 23 0 3 440 377 null 2 404 307 1 23 0 2 440 2559 null 2 404 307 1 23 0 1 526 32 null 2 603 325 8 237 0 2 526 1222 null 2 603 325 8 237 0 3 526 2570 null 2 603 325 8 237 0 1 292 103 249 2 92 284 14 129 0 2 292 1163 249 2 92 284 14 129 0 1 190 421 null 2 451 247 37 48 0 1 190 1614 null 2 451 247 37 48 0 2 680 63 null 2 492 379 39 198 0 2 680 378 null 2 492 379 39 198 0 3 680 2399 null 2 492 379 39 198 0 1 421 1271 180 2 712 465 49 60 0 2 421 1311 180 2 712 465 49 60 0 3 421 1961 null 2 712 465 49 60 0 1 311 81 null 2 647 67 52 220 0 4 311 1155 null 2 647 67 52 220 0 1 311 1703 null 2 647 67 52 220 0 2 311 2172 null 2 647 67 52 220 0 3 279 935 null 2 65 482 53 18 0 1 279 2244 null 2 65 482 53 18 0 2 77 478 380 2 571 20 57 124 0 1 77 2851 380 2 571 20 57 124 0 2 137 1089 211 2 677 333 63 55 0 3 137 1169 314 2 677 333 63 55 0 4 137 1488 314 2 677 333 63 55 0 2 137 1885 null 2 677 333 63 55 0 1 261 74 586 2 186 158 66 183 0 1 261 2046 586 2 186 158 66 183 0 2 392 529 443 2 192 209 86 57 0 4 392 804 443 2 192 209 86 57 0 2 392 1047 null 2 192 209 86 57 0 7 392 1527 null 2 192 209 86 57 0 6 392 1568 443 2 192 209 86 57 0 1 392 2025 null 2 192 209 86 57 0 5 392 2357 443 2 192 209 86 57 0 3 645 306 771 2 160 491 88 299 0 3 645 687 229 2 160 491 88 299 0 5 645 1179 229 2 160 491 88 299 0 2 645 2376 771 2 160 491 88 299 0 1 645 2661 229 2 160 491 88 299 0 4 10 10 37 2 268 176 89 8 0 1 10 1803 469 2 268 176 89 8 0 2 246 269 null 2 55 98 97 8 0 2 246 1518 null 2 55 98 97 8 0 3 246 1977 null 2 55 98 97 8 0 5 246 2412 null 2 55 98 97 8 0 1 246 2413 null 2 55 98 97 8 0 4 357 850 207 2 240 447 109 192 0 3 357 1096 188 2 240 447 109 192 0 2 357 1269 739 2 240 447 109 192 0 1 307 1992 null 2 184 30 118 104 0 1 579 541 251 2 93 115 121 345 0 2 579 1835 251 2 93 115 121 345 0 3 579 2350 null 2 93 115 121 345 0 1 242 1218 358 2 8 390 123 63 0 2 242 2489 358 2 8 390 123 63 0 1 315 47 null 2 365 102 127 4 0 2 315 853 null 2 365 102 127 4 0 4 315 1757 null 2 365 102 127 4 0 3 315 2423 null 2 365 102 127 4 0 1 87 230 null 2 153 449 128 60 0 4 87 1344 null 2 153 449 128 60 0 2 87 1557 null 2 153 449 128 60 0 1 87 2554 null 2 153 449 128 60 0 3 534 463 290 2 408 453 135 131 0 3 534 1000 290 2 408 453 135 131 0 4 534 1034 290 2 408 453 135 131 0 2 534 2271 290 2 408 453 135 131 0 1 76 956 null 2 23 301 152 97 0 1 76 1230 null 2 23 301 152 97 0 2 76 2834 null 2 23 301 152 97 0 3 322 890 170 2 589 230 155 13 0 3 322 1676 170 2 589 230 155 13 0 4 322 1806 170 2 589 230 155 13 0 1 322 2676 170 2 589 230 155 13 0 2 578 231 758 2 30 403 169 144 0 3 578 375 758 2 30 403 169 144 0 1 578 724 758 2 30 403 169 144 0 4 578 1409 null 2 30 403 169 144 0 6 578 1978 758 2 30 403 169 144 0 5 578 2267 758 2 30 403 169 144 0 2 276 386 null 2 575 24 178 5 0 1 276 869 null 2 575 24 178 5 0 2 276 1439 null 2 575 24 178 5 0 3 276 1701 null 2 575 24 178 5 0 4 624 1781 null 2 498 258 186 134 0 1 624 1817 null 2 498 258 186 134 0 2 624 2549 null 2 498 258 186 134 0 3 591 1746 null 2 645 8 187 280 0 1 591 2346 null 2 645 8 187 280 0 3 591 2746 null 2 645 8 187 280 0 2 505 2367 null 2 519 19 198 44 0 1 505 2787 null 2 519 19 198 44 0 2 457 911 null 2 131 140 208 29 0 2 457 1188 null 2 131 140 208 29 0 4 457 1872 null 2 131 140 208 29 0 3 457 2487 null 2 131 140 208 29 0 1 372 350 null 2 41 43 210 261 0 2 372 2053 null 2 41 43 210 261 0 3 372 2715 null 2 41 43 210 261 0 1 71 1147 null 2 444 231 211 10 0 1 71 1263 475 2 444 231 211 10 0 2 71 2534 475 2 444 231 211 10 0 3 386 213 null 2 488 304 225 38 0 2 386 485 null 2 488 304 225 38 0 3 386 936 null 2 488 304 225 38 0 5 386 1380 null 2 488 304 225 38 0 1 386 2090 null 2 488 304 225 38 0 4 386 2253 null 2 488 304 225 38 0 6 455 1109 null 2 259 395 229 29 0 2 455 1241 null 2 259 395 229 29 0 6 455 1458 null 2 259 395 229 29 0 1 455 2059 null 2 259 395 229 29 0 3 455 2160 null 2 259 395 229 29 0 5 455 2222 null 2 259 395 229 29 0 4

### Queries

In [0]:
query = f"""
SELECT 
    publ_id, author_id FROM publications
LIMIT 
    10;

"""

# Execute query
result_df = spark.sql("SELECT publ_id, author_id FROM DBLP_fact_table LIMIT 10")
display(result_df)

publ_id author_id 440 36 440 377 440 2559 526 32 526 1222 526 2570 292 103 292 1163 190 421 190 1614

In [0]:
#Retrieve the top 10 authors with the highest number of publications:
query = f"""
SELECT 
    Authors.first_name, Authors.last_name, COUNT(*) AS num_publications
FROM 
    DBLP_fact_table as MainTable
    INNER JOIN Authors ON MainTable.author_id = Authors.author_id 
GROUP BY 
    Authors.first_name, Authors.last_name 
ORDER BY 
    num_publications DESC 
LIMIT 
    10;

"""

# Execute query
result_df = spark.sql(query)
display(result_df)

first_name last_name num_publications Guang-zhong Yang 4 Wei Liu 4 Fanhua Shang 4 Gang Shen 2 Wei-ying Ma 2 Bhiksha Raj 2 Giancarlo Succi 2 Francisco Romero 2 Jian Liu 2 Haikal Abed 2

In [0]:
# Query to retrieve the authors who have published venue:
query = f"""
SELECT a.first_name, a.last_name, v.venue
FROM Authors a 
JOIN DBLP_fact_table as MainTable 
ON MainTable.author_id = a.author_id
JOIN Publications p 
ON p.publ_id = MainTable.publ_id
JOIN venues v 
ON v.venue_id = MainTable.venue_id

"""

# Execute query
result_df = spark.sql(query)
display(result_df)

first_name last_name venue Andreas Herzig 2013 Twenty-Eighth Annual IEEE/ACM Symposium on Logic in Computer Science (LICS 2013) Wanda Pratt CSCW '12: Computer Supported Cooperative Work Ali Makhdoumi 2013 51st Annual Allerton Conference on Communication, Control, and Computing (Allerton) Amara Amara 4th IEEE International Symposium on Electronic Design, Test and Applications (delta 2008) Xu Wu ICC 2013 - 2013 IEEE International Conference on Communications Kazuo Takahata 2011 International Conference on Computational Science and Its Applications (ICCSA) Darrell Long IEEE International Conference on Communications Barath Raghavan HotNets-XI: 11th ACM Workshop on Hot Topics in Networks Rosanne Price 2004 Australian Software Engineering Conference. Proceedings. Fanhua Shang KDD '12: The 18th ACM SIGKDD International Conference on Knowledge Discovery and Data Mining Fanhua Shang KDD '12: The 18th ACM SIGKDD International Conference on Knowledge Discovery and Data Mining Fanhua Shang KDD '12: The 18th ACM SIGKDD International Conference on Knowledge Discovery and Data Mining Fanhua Shang KDD '12: The 18th ACM SIGKDD International Conference on Knowledge Discovery and Data Mining M. Llorens SAC'10: The 2010 ACM Symposium on Applied Computing Radu Prodan 2010 11th IEEE/ACM International Conference on Grid Computing (GRID) Daniel Alexander 2008 5th IEEE International Symposium on Biomedical Imaging (ISBI 2008) Asfandyar Qureshi MobiSys05: The 3rd International Conference on Mobile Systems, Applications and Services 2005 Dominique Guinard Factory Automation (ETFA 2010) Bastien Giraud 4th IEEE International Symposium on Electronic Design, Test and Applications (delta 2008) Haikal Abed 2010 International Conference on Frontiers in Handwriting Recognition (ICFHR) Haikal Abed 2010 International Conference on Frontiers in Handwriting Recognition (ICFHR) Jakub Kukul 2012 IEEE 12th International Conference on Data Mining Workshops Malcolm Davidson IGARSS 2011 - 2011 IEEE International Geoscience and Remote Sensing Symposium Fabian Monrose 11th IEEE Symposium on Computers and Communications (ISCC'06) Renato Quintao MASCOTS 2000. Eighth International Symposium on Modeling, Analysis and Simulation and Telecommunication Systems Andreas Birk 2009 IEEE/RSJ International Conference on Intelligent Robots and Systems (IROS 2009) Andreas Rauber JCDL08: Joint Conference on Digital Libraries François Pierrot 5th IEEE-RAS International Conference on Humanoid Robots, 2005. Stefan Hasenauer IGARSS 2008 - 2008 IEEE International Geoscience and Remote Sensing Symposium Stefan Hasenauer IGARSS 2008 - 2008 IEEE International Geoscience and Remote Sensing Symposium Takeo Ohgane IEEE Vehicular Technology Conference Travis Abbott 2012 IEEE Congress on Evolutionary Computation (CEC) Tychy Anaya 2010 Seventh International Conference on Information Technology: New Generations Mozafar Mohammadi 2013 6th Joint IFIP Wireless and Mobile Networking Conference (WMNC 2013) Suk Seo ACM SE06: ACM Southeast Regional Conference Suk Seo ACM SE06: ACM Southeast Regional Conference Chuan-chia Huang 2012 13th International Symposium on Quality Electronic Design (ISQED) Chang-tzu Lin 2012 13th International Symposium on Quality Electronic Design (ISQED) Xiaofeng Wang CCS '09: 16th ACM Conference on Computer and Communications Security 2009 Guanhua Yan WebSci '12: Web Science 2012 H. Zimmer ICCAD-2005. IEEE/ACM International Conference on Computer-Aided Design, 2005. Florin Pop 2008 International Conference on Complex, Intelligent and Software Intensive Systems Hans Bonekamp IGARSS 2008 - 2008 IEEE International Geoscience and Remote Sensing Symposium Hans Bonekamp IGARSS 2008 - 2008 IEEE International Geoscience and Remote Sensing Symposium Patrick Mcdaniel 11th IEEE Symposium on Computers and Communications (ISCC'06) Lance Fortnow Proceedings 42nd IEEE Symposium on Foundations of Computer Science Inger Tøndel 2009 International Conference on Availability, Reliability and Security A

In [0]:
#Retrieve the publications with the highest number of citations:
query = f"""
SELECT 
    Publications.Title,
    CAST(Publications.n_citation AS INT) AS n_citation
FROM 
    Publications
ORDER BY 
    n_citation DESC;

"""

# Execute query
result_df = spark.sql(query)
display(result_df)

Title n_citation NUPACK: Analysis and design of nucleic acid systems 1069 A Regular Layout for Parallel Adders 695 Stabilization of switched continuous-time systems with all modes unstable via dwell time switching 338 Analysis of multicomponent LFM signals by a combined Wigner-Hough transform 322 The Diffusion Limit of Transport Equations Derived from Velocity-Jump Processes 258 Entropy, similarity measure of interval-valued intuitionistic fuzzy sets and their applications 244 Learning By Teaching: A New Agent Paradigm For Educational Software 235 Prediction error method for second-order blind identification 215 The extended Kalman filter as an exponential observer for nonlinear systems 201 A class of data structures for assoclat~ve searclung 194 Efficient informative sensing using multiple robots 191 On the complexity cost of disjunctive logic programming: Propositional case 182 Why do people play social network games? 175 Functional connectivity and coactivation of the nucleus accumbens: a combined functional connectivity and structure-based meta-analysis. 170 A retrospective look at PD projects 169 A word at a time: computing word relatedness using temporal semantic analysis 165 The discrete memoryless multiple-access channel with cribbing encoders 162 Robust Speaker Recognition in Noisy Conditions 161 Learning Distance Metrics with Contextual Constraints for Image Retrieval 158 Genetic algorithm solution for a risk-based partner selection problem in a virtual enterprise 150 Energy-Efficient Neuron, Synapse and STDP Integrated Circuits. 139 Modeling of Node Energy Consumption for Wireless Sensor Networks. 138 Nash-Cournot Equilibria in Electric Power Markets with Piecewise Linear Demand Functions and Joint Constraints 136 Learning your identity and disease from research papers: information leaks in genome wide association study 133 A reverse logistics decisions conceptual framework 133 An Off-line Signature Verification System Based on Fusion of Local and Global Information 128 Designing Unimodular Codes via Quadratic Optimization is not Always Hard 126 Effects of Text Structure and Prior Knowledge of the Learner on Navigation in Hypertext 126 Containment of misinformation spread in online social networks 121 A Multi-focus Image Fusion Method Based on Laplacian Pyramid. 119 Sum-capacity computation for the Gaussian vector broadcast channel via dual decomposition 115 Uniform Dynamic Self-Stabilizing Leader Election 111 Universally Composable Efficient Multiparty Computation from Threshold Homomorphic Encryption 111 Agglomerative hierarchical clustering with constraints: theoretical and empirical results 109 A text-based approach to feature modelling: Syntax and semantics of TVL 108 User Involvement as an Interaction Process: A Case Study 108 A Remote Laboratory in Engineering Measurement 106 ABLE: a toolkit for building multiagent autonomic systems 106 Software-defined internet architecture: decoupling architecture from infrastructure 99 Neuroanatomical analysis of the BTBR mouse model of autism using magnetic resonance imaging and diffusion tensor imaging. 98 The Role of Process in a Software Start-up 98 Deterministic Construction of Compressed Sensing Matrices via Algebraic Curves 97 Feedback stabilization for high order feedforward nonlinear time-delay systems 97 A multi-agent system for distributed multi-project scheduling: An auction-based negotiation approach 95 Interface behavior of compressible Navier-Stokes equations with vacuum 95 Synthesis of H INFINITY PID controllers: A parametric approach 93 Using redundancy to cope with failures in a delay tolerant network 91 Nonlinear index coding outperforming the linear optimum 89 Causal Factors Implicated in Research Misconduct: Evidence from ORI Case Files 87 Accelerating reinforcement learning through implicit imitation 87 RF Tunable Bandstop Filters With Constant Bandwidth Based on a Doublet Configuration. 86 Drivers of knowledge management in the corporate environment.

In [0]:
# Retrieve the authors with publications
query = f"""
SELECT 
    Authors.author_id, DBLP_fact_table.publ_id, Authors.first_name, Authors.last_name, Publications.title, Publications.n_citation, fos.fos
FROM Authors 
INNER JOIN DBLP_fact_table ON Authors.author_id = DBLP_fact_table.author_id
INNER JOIN Publications ON DBLP_fact_table.publ_id = Publications.publ_id
INNER JOIN fos ON DBLP_fact_table.fos_id = fos.fos_id
ORDER BY Authors.first_name, Authors.last_name;

"""

# Execute query
result_df = spark.sql(query)
display(result_df)

author_id publ_id first_name last_name title n_citation fos 1303 14 A Offutt An Analysis Tool for Coupling-Based Integration Testing 4 List(System integration testing, Programming language, Integration testing, Computer science, System testing, Manual testing, Non-regression testing, Java, Test strategy, Keyword-driven testing) 2430 194 A. Arslan Analysis of active and passive microwave observations from the NoSREx campaign. 5 List(Water equivalent, Radar, Meteorology, Microwave, Ku band, Synthetic aperture radar, Backscatter, Remote sensing, Environmental science, Snowpack, Snow) 1308 556 A. Bouchi An Object Observation for a Java Adaptative Distributed Application Platform 12 List(Load management, Distributed object, Object-oriented programming, Computer science, Load balancing (computing), Java concurrency, Real-time computing, Resource allocation, Application software, Java, Distributed computing) 1210 3 A. Cameron A bayesian decision theoretic approach for adaptive goal-directed sensing 11 List(Robot vision, Intelligent sensor, Computer science, Robustness (computer science), Artificial intelligence, Decision theory, Robot vision systems, Bayes estimator, Machine learning, Bayesian probability) 2119 326 A. Giulieri Analysis of on-line self-testing policies for real-time embedded multiprocessors in DSM technologies 8 List(Resource management, Digital electronics, Scheduling (computing), Computer science, Fault detection and isolation, Resource allocation, Integrated circuit, MPSoC, Embedded system, Built-in self-test) 1034 534 Abhishek Sharma Data insufficiency in sketch versus photo face recognition. 8 List(Training set, Facial recognition system, Image matching, Computer science, Element (criminal law), Speech recognition, Feature extraction, Suspect, Law enforcement, Sketch) 2854 338 Aca Gacic Detection of anomalous events from unlabeled sensor data in smart building environments. 7 List(Anomaly detection, Data modeling, Data mining, Minimum message length, False alarm, Dimensionality reduction, Pattern recognition, Computer science, Feature extraction, Unsupervised learning, Artificial intelligence, Mixture model) 350 372 Ada Diaconescu Controlling Self-Organising Software Applications with Archetypes 11 List(Survivability, Computer science, Software agent, Software prototyping, Software system, Software, Software architecture, Software quality, Operating system, Software development, Distributed computing) 2367 505 Aeron Buchanan Combining local and global motion models for feature point tracking 12 List(Computer vision, Pattern recognition, Computer science, Segmentation, Image noise, Feature extraction, Robustness (computer science), Image segmentation, Statistical model, Artificial intelligence, Application software, Cognitive neuroscience of visual object recognition) 1141 109 Aharon Bar-hillel Workstation capacity tuning using reinforcement learning 6 List(Multithreading, Permission, Markov process, Grid computing, Computer science, Server, Workstation, Throughput, Reinforcement learning, Distributed computing) 1043 70 Akhil Mathur Exploring playback and recording of web-based audio media on low-end feature phones 4 List(Information system, User experience design, Computer science, Phone, Web application, Multimedia, Sound recording and reproduction, Audio Media, Feature phone, The Internet) 2489 242 Akshar Bharati A karaka based approach to parsing of Indian languages 10 List(Verb, Top-down parsing, Programming language, Computer science, Machine translation, Finite-state machine, Constraint satisfaction problem, Karaka, Natural language processing, Artificial intelligence, Parsing, Parser combinator) 1806 322 Alexandre Renaux THE BAYESIAN ABEL BOUND ON THE MEAN SQUARE ERROR 13 List(Applied mathematics, Chapman–Robbins bound, Mathematical optimization, Upper and lower bounds, Signal-to-noise ratio, Mean squared error, Constrained optimization problem, Estimation theory, Mathematics, Bayesian probability, Constra

In [0]:
# Retrieve the the number of publication and the total number of citations for each author:
query = f"""
SELECT 
    Authors.first_name, 
    Authors.last_name, 
    COUNT(DISTINCT DBLP_fact_table.publ_id) AS num_publications, 
    SUM(Publications.n_citation) AS total_citations
FROM Authors 
INNER JOIN DBLP_fact_table ON Authors.author_id = DBLP_fact_table.author_id
INNER JOIN Publications ON DBLP_fact_table.publ_id = Publications.publ_id
GROUP BY Authors.first_name, Authors.last_name
ORDER BY num_publications DESC;

"""

# Execute query
result_df = spark.sql(query)
display(result_df)

first_name last_name num_publications total_citations Guang-zhong Yang 2 38.0 Chrisila Pettey 1 6.0 Hao Guo 1 5.0 John Gore 1 4.0 Christoph Becker 1 20.0 Jonghyun Choi 1 8.0 Zhenguo Li 1 44.0 Shigenori Inagaki 1 3.0 Patrick Mcdaniel 1 5.0 Amara Amara 1 4.0 Michael Lyu 1 158.0 Carole Delporte-gallet 1 23.0 Jingjing Chen 1 5.0 Xiaofeng Wang 1 133.0 Frédéric Delaunay 1 3.0 Shivam Agarwal 1 4.0 Rashina Hoda 1 3.0 Robert Sabourin 1 5.0 Heidar Talebi 1 3.0 Przemyslaw Kazienko 1 12.0 B. Jang 1 3.0 M. Schafer 1 22.0 B. Toursel 1 12.0 Nicolas Fel 1 3.0 Cody Watts 1 3.0 G. Neumann 1 6.0 Ronghuai Huang 1 3.0 Bhiksha Raj 1 30.0 Jacob Chakareski 1 7.0 Apoorv Srivastava 1 3.0 S. Wang 1 4.0 Ying-zong Huang 1 17.0 Olga Vechtomova 1 4.0 John Higgins 1 15.0 Carlos Ordonez 1 4.0 Bonnie John 1 7.0 Barath Raghavan 1 99.0 L.c. Jiao 1 13.0 Kevin Shum 1 6.0 M. Llorens 1 3.0 George Mylonas 1 15.0 Gary Bishop 1 36.0 Deepu Rajan 1 4.0 Sajal Das 1 14.0 Photios Ioannou 1 3.0 Dirk Schuettemeyer 1 5.0 Nicolas Tsingos 1 24.0 Dongyao Wang 1 49.0 Abhishek Sharma 1 8.0 Mojtaba Soorki 1 3.0 Steven Hoi 1 158.0 Chih-hao Chen 1 6.0 Liat Ein-dor 1 6.0 Aviel Rubin 1 5.0 Juha Kela 1 32.0 Nian-feng Tzeng 1 7.0 Kai Arras 1 82.0 Shih-ying Liu 1 5.0 Ziad Sakr 1 3.0 Stephan Stilkerich 1 3.0 Sophie Qiu 1 5.0 Renato Quintao 1 3.0 Jungsoon Yoo 1 6.0 Gian Tipaldi 1 82.0 Nathan Adams 1 5.0 Petar Popovski 1 7.0 Hannes Kulovits 1 20.0 Jonqlan Lin 1 4.0 Takao Terano 1 3.0 Eugene Agichtein 1 165.0 Predrag Spasojevic 1 63.0 Greg Welch 1 36.0 Patrick White 1 46.0 Hung-ming Chen 1 5.0 Padmini Jaikumar 1 7.0 Eric Granger 1 5.0 N. Ventroux 1 8.0 H. Wu 1 11.0 Girish Krishnan 1 77.0 Saeid Nahavandi 1 12.0 Tim Wright 1 3.0 Xin Zhang 1 8.0 Nadia Fawaz 1 42.0 Genady Grabarnik 1 8.0 Burton Andrews 1 7.0 J Oremtem 1 194.0 Eng Chng 1 4.0 Suk Seo 1 6.0 Travis Abbott 1 14.0 Kimon Valavanis 1 7.0 Y. Guo 1 17.0 Heiko Bülow 1 22.0 Jiyong Pang 1 49.0 Shonali Krishnaswamy 1 7.0 Ali Makhdoumi 1 42.0 Naoki Shibata 1 3.0 Cory Moody 1 5.0 Jehan-françois Pâris 1 6.0 Jakub Kukul 1 12.0 M. Glesner 1 22.0 Xiaoyong Zhou 1 133.0 Lianghao Han 1 14.0 Peter Luh 1 10.0 Guobiao Song 1 13.0 J. Guilhemsang 1 8.0 Haixu Tang 1 133.0 Manik Das 1 54.0 Walterio Mayol 1 29.0 Kathryn Daltorio 1 22.0 Juha Lemmetyinen 1 5.0 Yadong Mu 1 44.0 Juho Vehvilainen 1 5.0 Jim O'leary 1 4.0 Philippe Forster 1 13.0 Charles Creusere 1 4.0 Angkul Kongmunvattana 1 7.0 Stanislav Gorb 1 22.0 Yossi Ittach 1 6.0 Eric Diller 1 22.0 Maheedhar Kolla 1 4.0 Sanjay Madria 1 4.0 Aniello Castiglione 1 13.0 James Alty 1 3.0 Sung Yoo 1 6.0 Marie-andree Doran 1 33.0 Suthep Madarasmi 1 5.0 Richard Garcia 1 7.0 Ali Ghodsi 1 99.0 Ruiming Zheng 1 8.0 Helmut Rott 1 5.0 Sophie Dupuis 1 3.0 Chuan-chia Huang 1 5.0 Thomas Fahringer 1 33.0 Keiichi Yasumoto 1 3.0 Thomy Mertzanidou 1 14.0 Wanggen Wan 1 3.0 Zeyang Dai 1 9.0 Wolfgang Wagner 1 4.0 David Mcdonald 1 4.0 Ehud Sharlin 1 3.0 Farshid Delgosha 1 4.0 Mark Ackerman 1 4.0 Dimitrios Soudris 1 3.0 Judy Hankins 1 6.0 Kelly Edwards 1 4.0 Thad Starner 1 6.0 Donald Gordon 1 3.0 Gerda Jelleschitz 1 23.0 Mehdi Ghasemi 1 4.0 Seyyed Nikravesh 1 3.0 Herbjørn Andresen 1 9.0 Taratip Suwannasart 1 19.0 Nam Nguyen 1 121.0 Weihua Sun 1 3.0 J. Oliver 1 3.0 Darrell Long 1 6.0 Timm Schoening 1 5.0 Hui Tong 1 3.0 Alexandre Renaux 1 13.0 Sean Munson 1 4.0 Fikret Gurgen 1 3.0 Yoshitaka Shibata 1 6.0 David Hawkes 1 14.0 Aca Gacic 1 7.0 Meliha Yetisgen-yildiz 1 4.0 Gen Cao 1 8.0 Cen Li 1 6.0 Joseph Ng 1 6.0 Ioannis Koutras 1 3.0 Chieh-jui Lee 1 5.0 Elif Aktolga 1 5.0 Lin Sang 1 8.0 Hermann Kaindl 1 7.0 Gang Shen 1 98.0 Joachim Anlauf 1 3.0 A. Giulieri 1 8.0 John Guttag 1 30.0 T. Mishima 1 34.0 Jianchao Han 1 5.0 Andrew Wilson 1 4.0 Muzzafer Chaudery 1 15.0 Kegen Yu 1 17.0 Wojciech Indyk 1 12.0 Fabien Marchi 1 13.0 John Hipwell 1 14.0 Stefan Langer 1 21.0 Mark Wachowiak 1 3.0 Karsten Sohr 1 12.0 Donna Ng 1 6.0 Sanjay Ahuja 1 3.0 Andreas Herzig 1 18.0 Bo Xiong 1 10.0 Roy Yates 1 63.0 Dimitrios Rigas 1 3.0 Nils Ehnert 1 5.0 D. Verkest 1 46

In [0]:
#Retrieve the top 5 most common set of keywords:
query = f"""
SELECT 
    Keywords.keywords, COUNT(*) AS num_occurrences
FROM 
    DBLP_fact_table as MainTable 
    INNER JOIN Keywords ON MainTable.keyw_id = Keywords.keyw_id 
GROUP BY 
    Keywords.keywords 
ORDER BY 
    num_occurrences DESC 
LIMIT 
    5;

"""

# Execute query
result_df = spark.sql(query)
display(result_df)

keywords num_occurrences [health, broad agendum, tangible design outcome, design idea, cscw community, crowdsourcing, design challenge, brainstorming design, patient-generated information, new idea, small multidisciplinary group work, online community, future work, new collaboration opportunity, patient, biomedical research, idea generation, bioinformatics] 13 [geophysical signal processing, hydrological techniques, inverse problems, microwave measurement, radar signal processing, remote sensing by radar, snow, spaceborne radar, synthetic aperture radar, AD 2009 11, Ku band SAR observations, NOSREX campaign, Nordic Snow Radar Experiment, SWE, X band SAR observations, active microwave observations, coarse scale passive microwave data inversion, high resolution two frequency SAR observations, passive microwave observations, snow water equivalent, snowpack backscattering properties, snowpack emission properties, spaceborne SAR imagery, Snow Water Equivalent, microwave emission, radar backscatter] 13 [circuit layout CAD, integrated circuit layout, logic CAD, network routing, network-on-chip, parallel architectures, 2D-mesh network-on-chip, IP cores, NoC architecture, component placement, deadlock-free routing algorithm, floorplanning method, high density layouts, highly adaptive routing algorithm, parallel computer architecture, routing theories] 8 [non-deterministic execution order, csp specification, industrial system, control flow graph, state explosion, recent proposal, data structure, csp] 8 [force control, mobile robots, biologically-inspired robot, climbing ability, climbing insects, distributed inward gripping, geckos, mobile robot, screenbot, spring forces, walking inverted robot] 7

In [0]:
#Retrieve the top 5 most popular sets of fields of study:
query = f"""
SELECT 
    fos.fos, COUNT(*) AS num_publications
FROM 
    DBLP_fact_table as MainTable   
    INNER JOIN fos ON MainTable.fos_id = fos.fos_id 
GROUP BY 
    fos.fos 
ORDER BY 
    num_publications DESC 
LIMIT 
    5;
"""
# Execute query
result_df = spark.sql(query)
display(result_df)

fos num_publications List(Brainstorming, World Wide Web, Online community, Computer-supported cooperative work, Multidisciplinary approach, Crowdsourcing, Sociology, Group work, Knowledge management, Ethnography) 13 List(Water equivalent, Radar, Meteorology, Microwave, Ku band, Synthetic aperture radar, Backscatter, Remote sensing, Environmental science, Snowpack, Snow) 13 List(Link-state routing protocol, Equal-cost multi-path routing, Multipath routing, Dynamic Source Routing, Enhanced Interior Gateway Routing Protocol, Computer science, Policy-based routing, Static routing, Routing table, Distributed computing) 8 List(Data structure, Control flow graph, Industrial systems, Computer science, Algorithm, Order by, Distributed computing) 8 List(Mobile computing, Web usability, Mobile search, Computer science, Usability engineering, Usability, Usability lab, Human–computer interaction, Cognitive walkthrough, Usability inspection, Multimedia) 7

In [0]:
# retrieve the total number of publications per year:
query = f"""
SELECT Dates.year, count(*) AS num_publications
FROM DBLP_fact_table
JOIN Publications ON DBLP_fact_table.publ_id = Publications.publ_id
JOIN Dates ON DBLP_fact_table.date_id = Dates.date_id
GROUP BY Dates.year
ORDER BY Dates.year ASC NULLS FIRST;
;
"""

# Execute query
result_df = spark.sql(query)
display(result_df)

year num_publications 1984 8 1990 36 1992 16 1993 50 1995 20 1998 135 1999 37 2000 192 2001 256 2002 205 2003 201 2004 172 2005 912 2006 499 2007 102 2008 296 2009 522 2010 352 2011 175 2012 288 2013 112

In [0]:
# the number of publications per type of publication:
query = f"""
SELECT type_id,types.type, COUNT(*) as num_publications
FROM types
GROUP BY type_id,types.type;
"""

# Execute query
result_df = spark.sql(query)
display(result_df)

type_id type num_publications 0 journal-article 556 3 conference paper 158 5 report 156 4 workshop 156 1 book-chapter 286 2 proceedings-article 455 6 book 156